In [26]:
# !pip install catboost

In [116]:
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
from imblearn.over_sampling import SMOTE
import lightgbm as lgb
from sklearn.metrics import accuracy_score, classification_report
from xgboost import XGBClassifier
from sklearn.metrics import classification_report, confusion_matrix
from sklearn.model_selection import train_test_split, RandomizedSearchCV
from sklearn.preprocessing import StandardScaler
from catboost import CatBoostClassifier, Pool
import catboost

# 데이터 불러오기 및 합치기

In [117]:
import pandas as pd
df = pd.read_excel('/Users/ahndongsu/Desktop/2023_2학기_캡스톤/데이터/2020-2022_mlb_rawdata.xlsx', engine='openpyxl')

df_kmeans_batter = pd.read_csv('/Users/ahndongsu/Desktop/kmeans_batter_by_thesis_pa50.csv')
df_kmeans_pitcher = pd.read_csv('/Users/ahndongsu/Desktop/kmeans_pitcher_by_gpt_pa50.csv')


In [439]:
print(df.columns)

Index(['pitch_type', 'game_date', 'release_speed', 'release_pos_x',
       'release_pos_z', 'player_name', 'batter', 'pitcher', 'events',
       'description', 'spin_dir', 'spin_rate_deprecated',
       'break_angle_deprecated', 'break_length_deprecated', 'zone', 'des',
       'game_type', 'stand', 'p_throws', 'home_team', 'away_team', 'type',
       'hit_location', 'bb_type', 'balls', 'strikes', 'game_year', 'pfx_x',
       'pfx_z', 'plate_x', 'plate_z', 'on_3b', 'on_2b', 'on_1b',
       'outs_when_up', 'inning', 'inning_topbot', 'hc_x', 'hc_y',
       'tfs_deprecated', 'tfs_zulu_deprecated', 'fielder_2', 'umpire', 'sv_id',
       'vx0', 'vy0', 'vz0', 'ax', 'ay', 'az', 'sz_top', 'sz_bot',
       'hit_distance_sc', 'launch_speed', 'launch_angle', 'effective_speed',
       'release_spin_rate', 'release_extension', 'game_pk', 'pitcher.1',
       'fielder_2.1', 'fielder_3', 'fielder_4', 'fielder_5', 'fielder_6',
       'fielder_7', 'fielder_8', 'fielder_9', 'release_pos_y',
       'estima

In [440]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 421879 entries, 0 to 421878
Data columns (total 92 columns):
 #   Column                           Non-Null Count   Dtype         
---  ------                           --------------   -----         
 0   pitch_type                       421687 non-null  object        
 1   game_date                        421879 non-null  datetime64[ns]
 2   release_speed                    421670 non-null  float64       
 3   release_pos_x                    421620 non-null  float64       
 4   release_pos_z                    421620 non-null  float64       
 5   player_name                      421879 non-null  object        
 6   batter                           421879 non-null  int64         
 7   pitcher                          421879 non-null  int64         
 8   events                           421879 non-null  object        
 9   description                      421879 non-null  object        
 10  spin_dir                         0 non-null 

In [441]:

# # 재필터 해보기 # 원인은 모르겠지만 행손실이 너무 많아. 
# df43 = df[~((df['batter'].isin(df['pitcher'])) | (df['pitcher'].isin(df['batter'])))]

# # 결과 확인
# print(df43)

In [442]:
# # 데이터프레임의 열 갯수 확인
# num_columns = df43.shape[0]
# num_columns

In [443]:
# # 'batter'가 'pitcher'를 한 경우 또는 'pitcher'가 'batter'를 한 경우
# condition = ((df['batter'].isin(df['pitcher'])) | (df['pitcher'].isin(df['batter'])))

# # 조건에 맞는 행만 선택
# df44 = df[condition]
# df44.tail()

In [444]:
# filter_df=df[~((df['pitch_type'] == 'EP') & df['batter'].isin(df['pitcher']))]
# filter_df


In [445]:
# #65마일 
# final_filter_data = df[~(df['release_speed'] < 65)]
# final_filter_data

In [446]:
## 새로운 조건 
filtered_df = (
    df[((df['game_date'].dt.year == 2022) & (df['release_speed'] >= 69.9)) |
       ((df['game_date'].dt.year == 2021) & (df['release_speed'] >= 64.7)) |
       ((df['game_date'].dt.year == 2020) & (df['release_speed'] >= 65))]
)


In [447]:
filtered_df.head()

pitch_type  game_date  release_speed  release_pos_x  release_pos_z  \
0         SL 2020-09-27           84.6          -2.20           6.49   
1         SL 2020-09-27           84.7          -2.33           6.41   
2         FF 2020-09-27           91.7          -2.13           6.48   
3         FF 2020-09-27           90.6          -2.28           6.33   
4         SL 2020-09-27           84.4          -1.93           6.52   

        player_name  batter  pitcher     events      description  spin_dir  \
0    Ozuna, Marcell  542303   601713  field_out    hit_into_play       NaN   
1  Freeman, Freddie  518692   601713  field_out    hit_into_play       NaN   
2     Albies, Ozzie  645277   601713     single    hit_into_play       NaN   
3   Inciarte, Ender  542255   601713       walk             ball       NaN   
4    Flowers, Tyler  452095   601713  strikeout  swinging_strike       NaN   

   spin_rate_deprecated  break_angle_deprecated  break_length_deprecated  \
0                   NaN                     NaN                      NaN   
1                   NaN                     NaN                      NaN   
2                   NaN                     NaN                      NaN   
3                   NaN                     NaN                      NaN   
4                   NaN                     NaN                      NaN   

   zone                                                des game_type stand  \
0   9.0  Marcell Ozuna lines out to second baseman Jona...         R     R   
1   8.0  Freddie Freeman lines out to right fielder Tzu...         R     L   
2   1.0  Ozzie Albies singles on a ground ball to right...         R     L   
3  14.0                              Ender Inciarte walks.         R     L   
4  14.0                Tyler Flowers strikes out swinging.         R     R   

  p_throws home_team away_team type  hit_location      bb_type  balls  \
0        R       ATL       BOS    X           4.0   line_drive      0   
1        R       ATL       BOS    X           9.0   line_drive      0   
2        R       ATL       BOS    X           4.0  ground_ball      2   
3        R       ATL       BOS    B           NaN          NaN      3   
4        R       ATL       BOS    S           2.0          NaN      2   

   strikes  game_year  pfx_x  pfx_z  plate_x  plate_z  on_3b     on_2b  \
0        2       2020   0.47   0.25     0.60     1.68    NaN  542255.0   
1        0       2020   0.78   0.10     0.09     1.79    NaN  542255.0   
2        1       2020  -0.63   1.57    -0.80     2.69    NaN       NaN   
3        1       2020  -0.75   1.45     0.84     2.07    NaN       NaN   
4        2       2020   0.56  -0.09     0.51     1.20    NaN       NaN   

      on_1b  outs_when_up  inning inning_topbot    hc_x    hc_y  \
0  645277.0             2       5           Bot  135.34  142.72   
1  645277.0             1       5           Bot  182.14   85.74   
2  542255.0             1       5           Bot  173.40  117.72   
3       NaN             1       5           Bot     NaN     NaN   
4       NaN             0       5           Bot     NaN     NaN   

   tfs_deprecated  tfs_zulu_deprecated  fielder_2  umpire  sv_id       vx0  \
0             NaN                  NaN     608700     NaN    NaN  5.662031   
1             NaN                  NaN     608700     NaN    NaN  4.107405   
2             NaN                  NaN     608700     NaN    NaN  4.790940   
3             NaN                  NaN     608700     NaN    NaN  9.395170   
4             NaN                  NaN     608700     NaN    NaN  4.596731   

          vy0       vz0         ax         ay         az  sz_top  sz_bot  \
0 -123.150074 -5.457570   3.733274  23.195655 -28.744663    3.42    1.66   
1 -123.239942 -4.671884   7.152201  24.011905 -30.468382    3.58    1.76   
2 -133.433602 -7.215444  -8.587217  27.139350 -12.003441    3.18    1.51   
3 -131.357045 -7.774516 -10.669152  28.733451 -13.878226    3.15    1.45   
4 -122.790400 -5.858114   4.805528  24

In [448]:
merged_data = filtered_df.merge(df_kmeans_batter, left_on='batter', right_on='player_id', how='inner')
merged_data.tail(10)

pitch_type  game_date  release_speed  release_pos_x  release_pos_z  \
413828         SL 2022-09-25           84.7          -3.51           5.39   
413829         FF 2022-09-25           94.6          -0.88           5.45   
413830         FF 2022-09-25           95.5          -2.38           5.67   
413831         FF 2022-09-24           97.1          -1.62           5.48   
413832         FF 2022-09-24           98.8          -1.54           5.57   
413833         SI 2022-09-24           90.1          -2.66           4.77   
413834         SI 2022-09-23           91.1          -1.33           5.65   
413835         CU 2022-09-18           80.4           0.81           6.21   
413836         CU 2022-09-18           78.1           1.27           6.23   
413837         FF 2022-09-18           91.6          -1.38           5.39   

         player_name  batter  pitcher     events      description  spin_dir  \
413828  Diaz, Jordan  672478   453286  strikeout  swinging_strike       NaN   
413829  Diaz, Jordan  672478   607625     single    hit_into_play       NaN   
413830  Diaz, Jordan  672478   622098     single    hit_into_play       NaN   
413831  Diaz, Jordan  672478   594798  field_out    hit_into_play       NaN   
413832  Diaz, Jordan  672478   594798     single    hit_into_play       NaN   
413833  Diaz, Jordan  672478   592866     double    hit_into_play       NaN   
413834  Diaz, Jordan  672478   605135     single    hit_into_play       NaN   
413835  Diaz, Jordan  672478   664285  strikeout  swinging_strike       NaN   
413836  Diaz, Jordan  672478   664285  strikeout  swinging_strike       NaN   
413837  Diaz, Jordan  672478   664208     single    hit_into_play       NaN   

        spin_rate_deprecated  break_angle_deprecated  break_length_deprecated  \
413828                   NaN                     NaN                      NaN   
413829                   NaN                     NaN                      NaN   
413830                   NaN                     NaN                      NaN   
413831                   NaN                     NaN                      NaN   
413832                   NaN                     NaN                      NaN   
413833                   NaN                     NaN                      NaN   
413834                   NaN                     NaN                      NaN   
413835                   NaN                     NaN                      NaN   
413836                   NaN                     NaN                      NaN   
413837                   NaN                     NaN                      NaN   

        zone                                                des game_type  \
413828  14.0                  Jordan Diaz strikes out swinging.         R   
413829   3.0  Jordan Diaz singles on a sharp ground ball to ...         R   
413830  12.0  Jordan Diaz singles on a line drive to right f...         R   
413831   4.0  Jordan Diaz flies out to right fielder Darin Ruf.         R   
413832   1.0  Jordan Diaz singles on a ground ball to shorts...         R   
413833  13.0  Jordan Diaz doubles (1) on a ground ball to le...         R   
413834   5.0  Jordan Diaz singles on a ground ball to third ...         R   
413835   8.0                  Jordan Diaz strikes out swinging.         R   
413836  14.0                  Jordan Diaz strikes out swinging.         R   
413837   1.0  Jordan Diaz singles on a line drive to center ...         R   

       stand p_throws home_team away_team type  hit_location      bb_type  \
413828     R        R       OAK       NYM    S           2.0          NaN   
413829     R        R       OAK       NYM    X           8.0  ground_ball   
413830     R        R       OAK       NYM    X           9.0   line_drive   
413831     R        R       OAK       NYM    X           9.0     fly_ball   
413832     R        R       OAK       NYM    X           6.0  ground_ball   
413833     R        R       OAK       NYM    X           7.0  ground_ball   
413834    

In [449]:
final_merged_data = merged_data.merge(df_kmeans_pitcher, left_on='pitcher', right_on='player_id', how='inner')
final_merged_data.head()

pitch_type  game_date  release_speed  release_pos_x  release_pos_z  \
0         SL 2020-09-27           84.6          -2.20           6.49   
1         CH 2020-09-27           85.7          -2.20           6.43   
2         CH 2020-09-27           92.1          -2.28           6.39   
3         FF 2022-08-10           91.9          -1.28           6.59   
4         FF 2022-08-10           94.6          -1.86           6.23   

      player_name  batter  pitcher     events    description  spin_dir  \
0  Ozuna, Marcell  542303   601713  field_out  hit_into_play       NaN   
1  Ozuna, Marcell  542303   601713  field_out  hit_into_play       NaN   
2  Ozuna, Marcell  542303   601713   home_run  hit_into_play       NaN   
3  Ozuna, Marcell  542303   601713   home_run  hit_into_play       NaN   
4  Ozuna, Marcell  542303   601713  strikeout  called_strike       NaN   

   spin_rate_deprecated  break_angle_deprecated  break_length_deprecated  \
0                   NaN                     NaN                      NaN   
1                   NaN                     NaN                      NaN   
2                   NaN                     NaN                      NaN   
3                   NaN                     NaN                      NaN   
4                   NaN                     NaN                      NaN   

   zone                                                des game_type stand  \
0   9.0  Marcell Ozuna lines out to second baseman Jona...         R     R   
1  13.0  Marcell Ozuna flies out sharply to center fiel...         R     R   
2   8.0  Marcell Ozuna homers (18) on a fly ball to lef...         R     R   
3   4.0  Marcell Ozuna homers (20) on a fly ball to cen...         R     R   
4   7.0               Marcell Ozuna called out on strikes.         R     R   

  p_throws home_team away_team type  hit_location     bb_type  balls  strikes  \
0        R       ATL       BOS    X           4.0  line_drive      0        2   
1        R       ATL       BOS    X           8.0    fly_ball      1        2   
2        R       ATL       BOS    X           NaN    fly_ball      0        1   
3        R       BOS       ATL    X           NaN    fly_ball      1        1   
4        R       BOS       ATL    S           2.0         NaN      3        2   

   game_year  pfx_x  pfx_z  plate_x  plate_z  on_3b     on_2b     on_1b  \
0       2020   0.47   0.25     0.60     1.68    NaN  542255.0  645277.0   
1       2020  -1.12   0.61    -0.82     1.46    NaN       NaN  518692.0   
2       2020  -1.17   1.18    -0.15     2.02    NaN       NaN       NaN   
3       2022  -0.50   1.67    -0.29     2.84    NaN  663586.0  592696.0   
4       2022  -0.42   1.74    -0.40     2.09    NaN       NaN       NaN   

   outs_when_up  inning inning_topbot    hc_x    hc_y  tfs_deprecated  \
0             2       5           Bot  135.34  142.72             NaN   
1             1       3           Bot   82.82   49.70             NaN   
2             2       1           Bot   53.73   12.99             NaN   
3             2       4           Top   90.73   39.98             NaN   
4             0       3           Top     NaN     NaN             NaN   

   tfs_zulu_deprecated  fielder_2  umpire  sv_id       vx0         vy0  \
0                  NaN     608700     NaN    NaN  5.662031 -123.150074   
1                  NaN     608700     NaN    NaN  5.584848 -124.600799   
2                  NaN     608700     NaN    NaN  7.988384 -133.817574   
3                  NaN     624512     NaN    NaN  3.623768 -133.801997   
4                  NaN     624512     NaN    NaN  4.781716 -137.445865   

        vz0         ax         ay         az  sz_top  sz_bot  hit_distance_sc  \
0 -5.457570   3.733274  23.195655 -28.744663    3.42    1.66            141.0   
1 -6.733544 -12.787409  25.612829 -24.596556    3.42    1.66            365.0   
2 -7.892991 -15.726827  25.901835 -16.523550    3.42    1.66            468.0   
3 -7.395100  -6.781099  26.203063 -10.718435    3.59

In [450]:
# # pandas 설정 변경: 모든 행과 열을 출력하도록 설정
# pd.set_option('display.max_rows', None)
# pd.set_option('display.max_columns', None)

final_merged_data.head()

pitch_type  game_date  release_speed  release_pos_x  release_pos_z  \
0         SL 2020-09-27           84.6          -2.20           6.49   
1         CH 2020-09-27           85.7          -2.20           6.43   
2         CH 2020-09-27           92.1          -2.28           6.39   
3         FF 2022-08-10           91.9          -1.28           6.59   
4         FF 2022-08-10           94.6          -1.86           6.23   

      player_name  batter  pitcher     events    description  spin_dir  \
0  Ozuna, Marcell  542303   601713  field_out  hit_into_play       NaN   
1  Ozuna, Marcell  542303   601713  field_out  hit_into_play       NaN   
2  Ozuna, Marcell  542303   601713   home_run  hit_into_play       NaN   
3  Ozuna, Marcell  542303   601713   home_run  hit_into_play       NaN   
4  Ozuna, Marcell  542303   601713  strikeout  called_strike       NaN   

   spin_rate_deprecated  break_angle_deprecated  break_length_deprecated  \
0                   NaN                     NaN                      NaN   
1                   NaN                     NaN                      NaN   
2                   NaN                     NaN                      NaN   
3                   NaN                     NaN                      NaN   
4                   NaN                     NaN                      NaN   

   zone                                                des game_type stand  \
0   9.0  Marcell Ozuna lines out to second baseman Jona...         R     R   
1  13.0  Marcell Ozuna flies out sharply to center fiel...         R     R   
2   8.0  Marcell Ozuna homers (18) on a fly ball to lef...         R     R   
3   4.0  Marcell Ozuna homers (20) on a fly ball to cen...         R     R   
4   7.0               Marcell Ozuna called out on strikes.         R     R   

  p_throws home_team away_team type  hit_location     bb_type  balls  strikes  \
0        R       ATL       BOS    X           4.0  line_drive      0        2   
1        R       ATL       BOS    X           8.0    fly_ball      1        2   
2        R       ATL       BOS    X           NaN    fly_ball      0        1   
3        R       BOS       ATL    X           NaN    fly_ball      1        1   
4        R       BOS       ATL    S           2.0         NaN      3        2   

   game_year  pfx_x  pfx_z  plate_x  plate_z  on_3b     on_2b     on_1b  \
0       2020   0.47   0.25     0.60     1.68    NaN  542255.0  645277.0   
1       2020  -1.12   0.61    -0.82     1.46    NaN       NaN  518692.0   
2       2020  -1.17   1.18    -0.15     2.02    NaN       NaN       NaN   
3       2022  -0.50   1.67    -0.29     2.84    NaN  663586.0  592696.0   
4       2022  -0.42   1.74    -0.40     2.09    NaN       NaN       NaN   

   outs_when_up  inning inning_topbot    hc_x    hc_y  tfs_deprecated  \
0             2       5           Bot  135.34  142.72             NaN   
1             1       3           Bot   82.82   49.70             NaN   
2             2       1           Bot   53.73   12.99             NaN   
3             2       4           Top   90.73   39.98             NaN   
4             0       3           Top     NaN     NaN             NaN   

   tfs_zulu_deprecated  fielder_2  umpire  sv_id       vx0         vy0  \
0                  NaN     608700     NaN    NaN  5.662031 -123.150074   
1                  NaN     608700     NaN    NaN  5.584848 -124.600799   
2                  NaN     608700     NaN    NaN  7.988384 -133.817574   
3                  NaN     624512     NaN    NaN  3.623768 -133.801997   
4                  NaN     624512     NaN    NaN  4.781716 -137.445865   

        vz0         ax         ay         az  sz_top  sz_bot  hit_distance_sc  \
0 -5.457570   3.733274  23.195655 -28.744663    3.42    1.66            141.0   
1 -6.733544 -12.787409  25.612829 -24.596556    3.42    1.66            365.0   
2 -7.892991 -15.726827  25.901835 -16.523550    3.42    1.66            468.0   
3 -7.395100  -6.781099  26.203063 -10.718435    3.59

### 클러스터 별 사람 이름보기

In [451]:
# Batter_Cluster_Label이 0인 행만 필터링합니다.
filtered_data = final_merged_data[final_merged_data['Batter_Cluster_Label'] == 0]


print(filtered_data['player_name'])

23             Flowers, Tyler
24             Flowers, Tyler
92                  Ruiz, Rio
93                  Ruiz, Rio
94                  Ruiz, Rio
95                  Ruiz, Rio
96                  Ruiz, Rio
97                  Ruiz, Rio
98                  Ruiz, Rio
123           Severino, Pedro
124           Severino, Pedro
125           Severino, Pedro
126           Severino, Pedro
127           Severino, Pedro
128           Severino, Pedro
129           Severino, Pedro
130           Severino, Pedro
131           Severino, Pedro
132           Severino, Pedro
133           Severino, Pedro
161             Núñez, Renato
162             Núñez, Renato
163               Stewart, DJ
164               Stewart, DJ
165               Stewart, DJ
166               Stewart, DJ
167               Stewart, DJ
168               Stewart, DJ
169               Stewart, DJ
170               Stewart, DJ
171               Stewart, DJ
172               Stewart, DJ
173               Stewart, DJ
174       

In [452]:
# pandas 설정 변경: 모든 행과 열을 출력하도록 설정
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)

# Batter_Cluster_Label이 0인 행만 필터링합니다.
filtered_data = final_merged_data[final_merged_data['Batter_Cluster_Label'] == 0]

# 결과를 출력합니다.
print(filtered_data['player_name'])


23             Flowers, Tyler
24             Flowers, Tyler
92                  Ruiz, Rio
93                  Ruiz, Rio
94                  Ruiz, Rio
95                  Ruiz, Rio
96                  Ruiz, Rio
97                  Ruiz, Rio
98                  Ruiz, Rio
123           Severino, Pedro
124           Severino, Pedro
125           Severino, Pedro
126           Severino, Pedro
127           Severino, Pedro
128           Severino, Pedro
129           Severino, Pedro
130           Severino, Pedro
131           Severino, Pedro
132           Severino, Pedro
133           Severino, Pedro
161             Núñez, Renato
162             Núñez, Renato
163               Stewart, DJ
164               Stewart, DJ
165               Stewart, DJ
166               Stewart, DJ
167               Stewart, DJ
168               Stewart, DJ
169               Stewart, DJ
170               Stewart, DJ
171               Stewart, DJ
172               Stewart, DJ
173               Stewart, DJ
174       

In [453]:
# Batter_Cluster_Label이 0인 행만 필터링합니다.
filtered_data = final_merged_data[final_merged_data['Batter_Cluster_Label'] == 1]

# unique 한 player_name 값을 출력합니다.
unique_player_names = filtered_data['player_name'].unique()

# 결과를 출력합니다.
print(unique_player_names)


['Ozuna, Marcell' 'Freeman, Freddie' 'Albies, Ozzie' 'Swanson, Dansby'
 'Duvall, Adam' 'Acuña Jr., Ronald' 'Riley, Austin' 'Mountcastle, Ryan'
 'Hays, Austin' 'Mullins, Cedric' 'Voit, Luke' 'LeMahieu, DJ'
 'Stanton, Giancarlo' 'Judge, Aaron' 'Aguilar, Jesús' 'Marte, Starling'
 'Lowe, Nathaniel' 'Renfroe, Hunter' 'Arozarena, Randy' 'Adames, Willy'
 'Lowe, Brandon' 'Realmuto, J.T.' 'Harper, Bryce' 'Hoskins, Rhys'
 'McCutchen, Andrew' 'Tellez, Rowdy' 'Guerrero Jr., Vladimir'
 'Gurriel Jr., Lourdes' 'Grichuk, Randal' 'Hernández, Teoscar'
 'Soto, Juan' 'Santander, Anthony' 'Bichette, Bo' 'Conforto, Michael'
 'Alonso, Pete' 'Nimmo, Brandon' 'Seager, Corey' 'Pollock, AJ'
 'Semien, Marcus' 'Murphy, Sean' 'Olson, Matt' 'Grossman, Robbie'
 'Trout, Mike' 'Walsh, Jared' 'Ohtani, Shohei' 'France, Ty' 'Tucker, Kyle'
 'Correa, Carlos' 'Altuve, Jose' 'Springer, George' 'Bregman, Alex'
 'Gallo, Joey' 'Seager, Kyle' 'Chapman, Matt' 'Brown, Seth'
 'Arenado, Nolan' 'García, Adolis' 'Alvarez, Yordan' 'Rizz

In [454]:
# Batter_Cluster_Label이 0인 행만 필터링합니다.
filtered_data = final_merged_data[final_merged_data['Batter_Cluster_Label'] == 4]

# unique 한 player_name 값을 출력합니다.
unique_player_names = filtered_data['player_name'].unique()

# 결과를 출력합니다.
print(unique_player_names)


['Inciarte, Ender' 'Sandoval, Pablo' 'Hechavarría, Adeiny' 'Wade, Tyler'
 'Tauchman, Mike' 'Tsutsugo, Yoshi' 'Panik, Joe' 'Camargo, Johan'
 'Velazquez, Andrew' 'Andujar, Miguel' 'Vogt, Stephen'
 'Simmons, Andrelton' 'Bemboom, Anthony' 'Hedges, Austin' 'Mayfield, Jack'
 'White, Evan' 'Chirinos, Robinson' 'Sierra, Magneuris' 'Davis, Jonathan'
 'Taveras, Leody' 'Gonzalez, Marwin' 'Cave, Jake' 'Mondesi, Adalberto'
 "O'Hearn, Ryan" 'Zimmer, Bradley' 'Jankowski, Travis' 'Gutiérrez, Kelvin'
 'Díaz, Isan' 'Pache, Cristian' 'Jones, Jahmai' 'Lagares, Juan'
 'Walls, Taylor' 'García, Robel' 'Garcia, Aramis' 'Marcano, Tucupita'
 'Wynns, Austin' 'McKenna, Ryan' 'Barrera, Luis' 'Martin, Richie'
 'Nevin, Tyler' 'Thompson, Bubba' 'Delay, Jason' 'Madris, Bligh'
 'Pinto, René' 'Aranda, Jonathan' 'Bride, Jonah' 'Sisco, Chance'
 'Perez, Michael' 'Gosselin, Phil' 'Kingery, Scott' 'Ford, Mike'
 'Davis, Chris' 'Cordero, Franchy' 'Duran, Jarren' 'Bruján, Vidal'
 'Celestino, Gilberto' 'Arias, Gabriel' 'Palacios

In [455]:
# Batter_Cluster_Label이 0인 행만 필터링합니다.
filtered_data = final_merged_data[final_merged_data['Pitcher_Cluster_Label'] == 0]

# unique 한 player_name 값을 출력합니다.
unique_player_names = filtered_data['pitcher'].unique()

# 결과를 출력합니다.
print(unique_player_names)

[543901 570488 503569 542914 519144 544727 571927 453172 571578 622253
 605347 621237 630023 657044 445213 664350 570632 605501 453562 621107
 501625 502154 642528 656756 493603 605177 664141 624133 656322 605452
 621348 623352 474463 605288 542947 643256 645261 571670 641835 621366
 612434 607229 607536 468504 621389 622491 665665 660787 666168 518553
 644364 641501 676477 664123 592767 573186 667463 641540 656061 669912
 594580 622072 643511 657277 663773 667297 472610 573124 640455 676879
 606131 663855 658551 676050 641712 663559 502043 570257 670059 660813
 668941 664092 573009 676969 519008 607231 650911 657612 489334 593974
 552640 676596 453265 669622 595014 624647 592789 664875 656234 663903
 641745 592716 608665 502171 663546 622065 628708 518397 686753 670955
 669920 665001 503449 615698 658431 642770 647315 595881 594311 605280
 664285 663385 669270 621121 676840 642092 642233 650828 518858 523260
 642701 664192 545064 642546 448855 680702 570240 592473 669160 642083
 59541

In [458]:
selected_columns = ['pitch_type', 'release_speed', 'release_pos_x', 'release_pos_z',
    'events', 'zone', 'stand', 'p_throws', 'balls', 'strikes',
    'pfx_x', 'pfx_z', 'plate_x', 'plate_z', 'outs_when_up',
    'inning', 'release_spin_rate', 'release_extension', 'release_pos_y',
    'at_bat_number', 'pitch_number', 'spin_axis','on_3b', 'on_2b', 'on_1b','bat_score','fld_score','Pitcher_Cluster_Label','Batter_Cluster_Label'
]

In [459]:
df_new = final_merged_data[selected_columns]
df_new.head()

print(df_new.value_counts('events'))

events
field_out                    163637
strikeout                     93817
single                        57771
walk                          33881
double                        17931
home_run                      12963
force_out                      8464
grounded_into_double_play      7653
hit_by_pitch                   4764
triple                         1516
fielders_choice                 895
double_play                     891
fielders_choice_out             653
strikeout_double_play           263
triple_play                      13
Name: count, dtype: int64


# 전처리

In [460]:
# df_new DataFrame에서 'on_3b', 'on_2b', 'on_1b' 열에 있는 NaN 값을 0으로 채우기
df_new['on_3b'].fillna(0, inplace=True)
df_new['on_2b'].fillna(0, inplace=True)
df_new['on_1b'].fillna(0, inplace=True)

# df_new DataFrame에서 'on_3b', 'on_2b', 'on_1b' 열에 있는 0을 제외한 값들을 1로 변환
df_new['on_3b'] = df_new['on_3b'].apply(lambda x: 1 if x != 0 else 0)
df_new['on_2b'] = df_new['on_2b'].apply(lambda x: 1 if x != 0 else 0)
df_new['on_1b'] = df_new['on_1b'].apply(lambda x: 1 if x != 0 else 0)
df_new

# FA 값 기타 공이므로 삭제
df_new.drop(df_new[df_new['pitch_type'] == 'FA'].index, inplace=True)

/var/folders/r1/znzmlx_d1xg065b8mc9v3v7r0000gn/T/ipykernel_24001/2331603607.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_new['on_3b'].fillna(0, inplace=True)
/var/folders/r1/znzmlx_d1xg065b8mc9v3v7r0000gn/T/ipykernel_24001/2331603607.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_new['on_2b'].fillna(0, inplace=True)
/var/folders/r1/znzmlx_d1xg065b8mc9v3v7r0000gn/T/ipykernel_24001/2331603607.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returnin

In [461]:
mapping = {
    'FF': 1, 'SI': 1, 'FC': 1,
    'SL': 2, 'KC': 2, 'CU': 2, 'CS': 2, 'KN': 2, 'EP': 2, 'SV': 2, 'ST': 2,
    'FS': 3, 'CH': 3, 'SC': 3
}

df_new['pitch_type'] = df_new['pitch_type'].replace(mapping)

# 출루 1, 아웃 0
mapping = {
    'single': 1, 'double': 1, 'triple': 1, 'home_run': 1, 'walk': 1, 'hit_by_pitch': 1,
    'field_out': 0, 'strikeout': 0, 'force_out': 0, 'grounded_into_double_play': 0,
    'double_play': 0, 'fielders_choice': 0, 'strikeout_double_play': 0,
    'fielders_choice_out': 0, 'triple_play': 0, 
}

df_new['events'] = df_new['events'].replace(mapping)

# 오른손 1, 왼손 2
mapping = {
    'R': 1,'L':2}

df_new['stand'] = df_new['stand'].replace(mapping)

# 오른손 1, 왼손 2
mapping = {
    'R': 1,'L':2}

df_new['p_throws'] = df_new['p_throws'].replace(mapping)
df_new.head()

/var/folders/r1/znzmlx_d1xg065b8mc9v3v7r0000gn/T/ipykernel_24001/1389741101.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_new['pitch_type'] = df_new['pitch_type'].replace(mapping)
/var/folders/r1/znzmlx_d1xg065b8mc9v3v7r0000gn/T/ipykernel_24001/1389741101.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_new['events'] = df_new['events'].replace(mapping)
/var/folders/r1/znzmlx_d1xg065b8mc9v3v7r0000gn/T/ipykernel_24001/1389741101.py:23: SettingWithCopyWarning: 
A value is trying to be set on a 

pitch_type  release_speed  release_pos_x  release_pos_z  events  zone  \
0           2           84.6          -2.20           6.49       0   9.0   
1           3           85.7          -2.20           6.43       0  13.0   
2           3           92.1          -2.28           6.39       1   8.0   
3           1           91.9          -1.28           6.59       1   4.0   
4           1           94.6          -1.86           6.23       0   7.0   

   stand  p_throws  balls  strikes  pfx_x  pfx_z  plate_x  plate_z  \
0      1         1      0        2   0.47   0.25     0.60     1.68   
1      1         1      1        2  -1.12   0.61    -0.82     1.46   
2      1         1      0        1  -1.17   1.18    -0.15     2.02   
3      1         1      1        1  -0.50   1.67    -0.29     2.84   
4      1         1      3        2  -0.42   1.74    -0.40     2.09   

   outs_when_up  inning  release_spin_rate  release_extension  release_pos_y  \
0             2       5             2299.0                6.8          53.74   
1             1       3             1647.0                6.9          53.65   
2             2       1             2233.0                6.6          53.87   
3             2       4             2300.0                6.8          53.68   
4             0       3             2330.0                6.8          53.66   

   at_bat_number  pitch_number  spin_axis  on_3b  on_2b  on_1b  bat_score  \
0             45             3      112.0      0      1      1          1   
1             28             5      221.0      0      0      1          1   
2              9             2      207.0      0      0      0          0   
3             28             3      194.0      0      1      1          0   
4             16             6      205.0      0      0      0          0   

   fld_score  Pitcher_Cluster_Label  Batter_Cluster_Label  
0          3                      5                     1  
1          1                      5                     1  
2          1                      5                     1  
3          0                      5                     1  
4          0                      5                     1

In [462]:
df_new.dropna(inplace=True)
nan_count = df_new.isnull().sum()
print("NaN 개수:", nan_count)

NaN 개수: pitch_type               0
release_speed            0
release_pos_x            0
release_pos_z            0
events                   0
zone                     0
stand                    0
p_throws                 0
balls                    0
strikes                  0
pfx_x                    0
pfx_z                    0
plate_x                  0
plate_z                  0
outs_when_up             0
inning                   0
release_spin_rate        0
release_extension        0
release_pos_y            0
at_bat_number            0
pitch_number             0
spin_axis                0
on_3b                    0
on_2b                    0
on_1b                    0
bat_score                0
fld_score                0
Pitcher_Cluster_Label    0
Batter_Cluster_Label     0
dtype: int64


/var/folders/r1/znzmlx_d1xg065b8mc9v3v7r0000gn/T/ipykernel_24001/594596374.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_new.dropna(inplace=True)


In [463]:
print(df_new.columns)

Index(['pitch_type', 'release_speed', 'release_pos_x', 'release_pos_z',
       'events', 'zone', 'stand', 'p_throws', 'balls', 'strikes', 'pfx_x',
       'pfx_z', 'plate_x', 'plate_z', 'outs_when_up', 'inning',
       'release_spin_rate', 'release_extension', 'release_pos_y',
       'at_bat_number', 'pitch_number', 'spin_axis', 'on_3b', 'on_2b', 'on_1b',
       'bat_score', 'fld_score', 'Pitcher_Cluster_Label',
       'Batter_Cluster_Label'],
      dtype='object')


In [464]:
# 'events' 열의 데이터 타입을 object로 변환
df_new['events'] = df_new['events'].astype(str)
df_new['stand'] = df_new['stand'].astype(str)
df_new['p_throws'] = df_new['p_throws'].astype(str)
df_new['pitch_type'] = df_new['pitch_type'].astype(str)


/var/folders/r1/znzmlx_d1xg065b8mc9v3v7r0000gn/T/ipykernel_24001/2551373172.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_new['events'] = df_new['events'].astype(str)
/var/folders/r1/znzmlx_d1xg065b8mc9v3v7r0000gn/T/ipykernel_24001/2551373172.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_new['stand'] = df_new['stand'].astype(str)
/var/folders/r1/znzmlx_d1xg065b8mc9v3v7r0000gn/T/ipykernel_24001/2551373172.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a

In [465]:
df_new.isnull().sum()

pitch_type               0
release_speed            0
release_pos_x            0
release_pos_z            0
events                   0
zone                     0
stand                    0
p_throws                 0
balls                    0
strikes                  0
pfx_x                    0
pfx_z                    0
plate_x                  0
plate_z                  0
outs_when_up             0
inning                   0
release_spin_rate        0
release_extension        0
release_pos_y            0
at_bat_number            0
pitch_number             0
spin_axis                0
on_3b                    0
on_2b                    0
on_1b                    0
bat_score                0
fld_score                0
Pitcher_Cluster_Label    0
Batter_Cluster_Label     0
dtype: int64

In [466]:
# # 커쇼 이벤트
# df_new_player = df_new[df_new['pitcher'] == 477132]

In [467]:
# # 커쇼
# df_new_player.head()


In [468]:
# df_new_player.value_counts('Batter_Cluster_Label')

In [469]:
# print(len(df_new_player[(df_new_player['Batter_Cluster_Label'] == 4) & (df_new_player['events'] == '1')]))



In [470]:
# print(17/91)

## Standard scaler

In [471]:
from sklearn.preprocessing import StandardScaler
import pandas as pd

# df_new: 원본 데이터 프레임

# 스케일링할 열 선택
columns_to_scale = ['release_speed', 'release_pos_x', 'release_pos_z', 'pfx_x', 'pfx_z',
                    'plate_x', 'plate_z', 'release_spin_rate', 'release_extension', 'release_pos_y', 'spin_axis']

# 스케일러 객체 생성
scaler = StandardScaler()

# 선택한 열에 대해 스케일 적용
scaled_data = scaler.fit_transform(df_new[columns_to_scale])

# 스케일된 데이터프레임 생성
scaled_df = pd.DataFrame(scaled_data, columns=columns_to_scale, index=df_new.index)

# 스케일링하지 않을 열 선택
columns_to_keep = [col for col in df_new.columns if col not in columns_to_scale]

# 원래 데이터 프레임에서 스케일링하지 않을 열 선택
df_remaining = df_new[columns_to_keep]

# 스케일이 적용된 데이터프레임과 원래 데이터프레임 합치기
final_df = pd.concat([df_remaining, scaled_df], axis=1)
print(final_df.isnull().sum())


pitch_type               0
events                   0
zone                     0
stand                    0
p_throws                 0
balls                    0
strikes                  0
outs_when_up             0
inning                   0
at_bat_number            0
pitch_number             0
on_3b                    0
on_2b                    0
on_1b                    0
bat_score                0
fld_score                0
Pitcher_Cluster_Label    0
Batter_Cluster_Label     0
release_speed            0
release_pos_x            0
release_pos_z            0
pfx_x                    0
pfx_z                    0
plate_x                  0
plate_z                  0
release_spin_rate        0
release_extension        0
release_pos_y            0
spin_axis                0
dtype: int64


In [472]:
final_df=df_new.copy()
df_new.head()

pitch_type  release_speed  release_pos_x  release_pos_z events  zone stand  \
0          2           84.6          -2.20           6.49      0   9.0     1   
1          3           85.7          -2.20           6.43      0  13.0     1   
2          3           92.1          -2.28           6.39      1   8.0     1   
3          1           91.9          -1.28           6.59      1   4.0     1   
4          1           94.6          -1.86           6.23      0   7.0     1   

  p_throws  balls  strikes  pfx_x  pfx_z  plate_x  plate_z  outs_when_up  \
0        1      0        2   0.47   0.25     0.60     1.68             2   
1        1      1        2  -1.12   0.61    -0.82     1.46             1   
2        1      0        1  -1.17   1.18    -0.15     2.02             2   
3        1      1        1  -0.50   1.67    -0.29     2.84             2   
4        1      3        2  -0.42   1.74    -0.40     2.09             0   

   inning  release_spin_rate  release_extension  release_pos_y  at_bat_number  \
0       5             2299.0                6.8          53.74             45   
1       3             1647.0                6.9          53.65             28   
2       1             2233.0                6.6          53.87              9   
3       4             2300.0                6.8          53.68             28   
4       3             2330.0                6.8          53.66             16   

   pitch_number  spin_axis  on_3b  on_2b  on_1b  bat_score  fld_score  \
0             3      112.0      0      1      1          1          3   
1             5      221.0      0      0      1          1          1   
2             2      207.0      0      0      0          0          1   
3             3      194.0      0      1      1          0          0   
4             6      205.0      0      0      0          0          0   

   Pitcher_Cluster_Label  Batter_Cluster_Label  
0                      5                     1  
1                      5                     1  
2                      5                     1  
3                      5                     1  
4                      5                     1

In [473]:
import pandas as pd

# 결측값이 있는 행 제거
df_new = df_new.dropna(subset=['events'])

df_new.info()
print(df_new.isnull().sum())


<class 'pandas.core.frame.DataFrame'>
Index: 403668 entries, 0 to 405111
Data columns (total 29 columns):
 #   Column                 Non-Null Count   Dtype  
---  ------                 --------------   -----  
 0   pitch_type             403668 non-null  object 
 1   release_speed          403668 non-null  float64
 2   release_pos_x          403668 non-null  float64
 3   release_pos_z          403668 non-null  float64
 4   events                 403668 non-null  object 
 5   zone                   403668 non-null  float64
 6   stand                  403668 non-null  object 
 7   p_throws               403668 non-null  object 
 8   balls                  403668 non-null  int64  
 9   strikes                403668 non-null  int64  
 10  pfx_x                  403668 non-null  float64
 11  pfx_z                  403668 non-null  float64
 12  plate_x                403668 non-null  float64
 13  plate_z                403668 non-null  float64
 14  outs_when_up           403668 non-null  i

In [474]:
from imblearn.over_sampling import SMOTE

# 종속변수와 독립변수 분리
 
X = df_new.drop('events', axis=1)  # 독립변수
y = df_new['events'] 


# SMOTE를 사용하여 오버샘플링
smote = SMOTE(random_state=42)  # SMOTE 객체 생성
X_resampled, y_resampled = smote.fit_resample(X, y)  # 오버샘플링된 데이터셋 생성

# 오버샘플링 후의 데이터셋 확인
print(f"오버샘플링 전 데이터: {len(df_new)} 건")
print(f"오버샘플링 후 데이터: {len(X_resampled)} 건")


오버샘플링 전 데이터: 403668 건
오버샘플링 후 데이터: 550604 건


In [475]:
X_resampled.head()

pitch_type  release_speed  release_pos_x  release_pos_z  zone stand  \
0        2.0           84.6          -2.20           6.49   9.0   1.0   
1        3.0           85.7          -2.20           6.43  13.0   1.0   
2        3.0           92.1          -2.28           6.39   8.0   1.0   
3        1.0           91.9          -1.28           6.59   4.0   1.0   
4        1.0           94.6          -1.86           6.23   7.0   1.0   

  p_throws  balls  strikes  pfx_x  pfx_z  plate_x  plate_z  outs_when_up  \
0      1.0      0        2   0.47   0.25     0.60     1.68             2   
1      1.0      1        2  -1.12   0.61    -0.82     1.46             1   
2      1.0      0        1  -1.17   1.18    -0.15     2.02             2   
3      1.0      1        1  -0.50   1.67    -0.29     2.84             2   
4      1.0      3        2  -0.42   1.74    -0.40     2.09             0   

   inning  release_spin_rate  release_extension  release_pos_y  at_bat_number  \
0       5             2299.0                6.8          53.74             45   
1       3             1647.0                6.9          53.65             28   
2       1             2233.0                6.6          53.87              9   
3       4             2300.0                6.8          53.68             28   
4       3             2330.0                6.8          53.66             16   

   pitch_number  spin_axis  on_3b  on_2b  on_1b  bat_score  fld_score  \
0             3      112.0      0      1      1          1          3   
1             5      221.0      0      0      1          1          1   
2             2      207.0      0      0      0          0          1   
3             3      194.0      0      1      1          0          0   
4             6      205.0      0      0      0          0          0   

   Pitcher_Cluster_Label  Batter_Cluster_Label  
0                      5                     1  
1                      5                     1  
2                      5                     1  
3                      5                     1  
4                      5                     1

In [476]:
y_resampled.head()

0    0
1    0
2    1
3    1
4    0
Name: events, dtype: object

In [477]:
import pandas as pd

# X_resampled와 y_resampled를 데이터프레임으로 변환
X_resampled_df = pd.DataFrame(X_resampled)
y_resampled_df = pd.DataFrame(y_resampled)  # 'target_column'은 적절한 컬럼명으로 변경해야 해

# X_resampled와 y_resampled를 합치기
df_new = pd.concat([X_resampled_df, y_resampled_df], axis=1)


In [478]:
df_new.head()
print(len(df_new))
print(df_new.head())

550604
  pitch_type  release_speed  release_pos_x  release_pos_z  zone stand  \
0        2.0           84.6          -2.20           6.49   9.0   1.0   
1        3.0           85.7          -2.20           6.43  13.0   1.0   
2        3.0           92.1          -2.28           6.39   8.0   1.0   
3        1.0           91.9          -1.28           6.59   4.0   1.0   
4        1.0           94.6          -1.86           6.23   7.0   1.0   

  p_throws  balls  strikes  pfx_x  pfx_z  plate_x  plate_z  outs_when_up  \
0      1.0      0        2   0.47   0.25     0.60     1.68             2   
1      1.0      1        2  -1.12   0.61    -0.82     1.46             1   
2      1.0      0        1  -1.17   1.18    -0.15     2.02             2   
3      1.0      1        1  -0.50   1.67    -0.29     2.84             2   
4      1.0      3        2  -0.42   1.74    -0.40     2.09             0   

   inning  release_spin_rate  release_extension  release_pos_y  at_bat_number  \
0       5       

# Kmeans mapping

In [479]:
# Define the list of cluster labels for pitchers and batters
pitcher_clusters = [0, 1, 2, 3, 4, 5]
batter_clusters = [0, 1, 2, 3, 4]

# Iterate through pitcher and batter cluster labels
for pitcher_label in pitcher_clusters:
    for batter_label in batter_clusters:
        # Filter the DataFrame based on the cluster labels
        filtered_df = df_new[(df_new['Pitcher_Cluster_Label'] == pitcher_label) & (df_new['Batter_Cluster_Label'] == batter_label)]

        # Count the event values
        event_counts = filtered_df['events'].value_counts()

        # Calculate the on-base ratio
        count_1 = event_counts.get(1, 0)
        count_0 = event_counts.get(0, 0)
        on_base_ratio = count_1 / (count_0 + count_1)

        # Define the variable name
        variable_name = f'On_base_ratio_{pitcher_label}vs{batter_label}'

        # Assign the on-base ratio to a global variable
        globals()[variable_name] = on_base_ratio

In [480]:
# 조건 1에 해당하는 행에 'On_base_ratio_0vs0' 값을 할당
df_new.loc[(df_new['Pitcher_Cluster_Label'] == 0) & (df_new['Batter_Cluster_Label'] == 0), 'On_base_ratio_by_pitcher_batter_type'] = On_base_ratio_0vs0

# 조건 2에 해당하는 행에 'On_base_ratio_0vs1' 값을 할당
df_new.loc[(df_new['Pitcher_Cluster_Label'] == 0) & (df_new['Batter_Cluster_Label'] == 1), 'On_base_ratio_by_pitcher_batter_type'] = On_base_ratio_0vs1

# 조건 1에 해당하는 행에 'On_base_ratio_0vs2' 값을 할당
df_new.loc[(df_new['Pitcher_Cluster_Label'] == 0) & (df_new['Batter_Cluster_Label'] == 2), 'On_base_ratio_by_pitcher_batter_type'] = On_base_ratio_0vs2

# 조건 2에 해당하는 행에 'On_base_ratio_0vs3' 값을 할당
df_new.loc[(df_new['Pitcher_Cluster_Label'] == 0) & (df_new['Batter_Cluster_Label'] == 3), 'On_base_ratio_by_pitcher_batter_type'] = On_base_ratio_0vs3

# 조건 2에 해당하는 행에 'On_base_ratio_0vs3' 값을 할당
df_new.loc[(df_new['Pitcher_Cluster_Label'] == 0) & (df_new['Batter_Cluster_Label'] == 4), 'On_base_ratio_by_pitcher_batter_type'] = On_base_ratio_0vs4

# 조건 1에 해당하는 행에 'On_base_ratio_0vs0' 값을 할당
df_new.loc[(df_new['Pitcher_Cluster_Label'] == 1) & (df_new['Batter_Cluster_Label'] == 0), 'On_base_ratio_by_pitcher_batter_type'] = On_base_ratio_1vs0

# 조건 2에 해당하는 행에 'On_base_ratio_0vs1' 값을 할당
df_new.loc[(df_new['Pitcher_Cluster_Label'] == 1) & (df_new['Batter_Cluster_Label'] == 1), 'On_base_ratio_by_pitcher_batter_type'] = On_base_ratio_1vs1

# 조건 1에 해당하는 행에 'On_base_ratio_0vs2' 값을 할당
df_new.loc[(df_new['Pitcher_Cluster_Label'] == 1) & (df_new['Batter_Cluster_Label'] == 2), 'On_base_ratio_by_pitcher_batter_type'] = On_base_ratio_1vs2

# 조건 2에 해당하는 행에 'On_base_ratio_0vs3' 값을 할당
df_new.loc[(df_new['Pitcher_Cluster_Label'] == 1) & (df_new['Batter_Cluster_Label'] == 3), 'On_base_ratio_by_pitcher_batter_type'] = On_base_ratio_1vs3

# 조건 2에 해당하는 행에 'On_base_ratio_0vs3' 값을 할당
df_new.loc[(df_new['Pitcher_Cluster_Label'] == 1) & (df_new['Batter_Cluster_Label'] == 4), 'On_base_ratio_by_pitcher_batter_type'] = On_base_ratio_1vs4

# 조건 1에 해당하는 행에 'On_base_ratio_0vs0' 값을 할당
df_new.loc[(df_new['Pitcher_Cluster_Label'] == 2) & (df_new['Batter_Cluster_Label'] == 0), 'On_base_ratio_by_pitcher_batter_type'] = On_base_ratio_2vs0

# 조건 2에 해당하는 행에 'On_base_ratio_0vs1' 값을 할당
df_new.loc[(df_new['Pitcher_Cluster_Label'] == 2) & (df_new['Batter_Cluster_Label'] == 1), 'On_base_ratio_by_pitcher_batter_type'] = On_base_ratio_2vs1

# 조건 1에 해당하는 행에 'On_base_ratio_0vs2' 값을 할당
df_new.loc[(df_new['Pitcher_Cluster_Label'] == 2) & (df_new['Batter_Cluster_Label'] == 2), 'On_base_ratio_by_pitcher_batter_type'] = On_base_ratio_2vs2

# 조건 2에 해당하는 행에 'On_base_ratio_0vs3' 값을 할당
df_new.loc[(df_new['Pitcher_Cluster_Label'] == 2) & (df_new['Batter_Cluster_Label'] == 3), 'On_base_ratio_by_pitcher_batter_type'] = On_base_ratio_2vs3

# 조건 2에 해당하는 행에 'On_base_ratio_0vs3' 값을 할당
df_new.loc[(df_new['Pitcher_Cluster_Label'] == 2) & (df_new['Batter_Cluster_Label'] == 4), 'On_base_ratio_by_pitcher_batter_type'] = On_base_ratio_2vs4

# 조건 1에 해당하는 행에 'On_base_ratio_0vs0' 값을 할당
df_new.loc[(df_new['Pitcher_Cluster_Label'] == 3) & (df_new['Batter_Cluster_Label'] == 0), 'On_base_ratio_by_pitcher_batter_type'] = On_base_ratio_3vs0

# 조건 2에 해당하는 행에 'On_base_ratio_0vs1' 값을 할당
df_new.loc[(df_new['Pitcher_Cluster_Label'] == 3) & (df_new['Batter_Cluster_Label'] == 1), 'On_base_ratio_by_pitcher_batter_type'] = On_base_ratio_3vs1

# 조건 1에 해당하는 행에 'On_base_ratio_0vs2' 값을 할당
df_new.loc[(df_new['Pitcher_Cluster_Label'] == 3) & (df_new['Batter_Cluster_Label'] == 2), 'On_base_ratio_by_pitcher_batter_type'] = On_base_ratio_3vs2

# 조건 2에 해당하는 행에 'On_base_ratio_0vs3' 값을 할당
df_new.loc[(df_new['Pitcher_Cluster_Label'] == 3) & (df_new['Batter_Cluster_Label'] == 3), 'On_base_ratio_by_pitcher_batter_type'] = On_base_ratio_3vs3

# 조건 2에 해당하는 행에 'On_base_ratio_0vs3' 값을 할당
df_new.loc[(df_new['Pitcher_Cluster_Label'] == 3) & (df_new['Batter_Cluster_Label'] == 4), 'On_base_ratio_by_pitcher_batter_type'] = On_base_ratio_3vs4

# 조건 1에 해당하는 행에 'On_base_ratio_0vs0' 값을 할당
df_new.loc[(df_new['Pitcher_Cluster_Label'] == 4) & (df_new['Batter_Cluster_Label'] == 0), 'On_base_ratio_by_pitcher_batter_type'] = On_base_ratio_4vs0

# 조건 2에 해당하는 행에 'On_base_ratio_0vs1' 값을 할당
df_new.loc[(df_new['Pitcher_Cluster_Label'] == 4) & (df_new['Batter_Cluster_Label'] == 1), 'On_base_ratio_by_pitcher_batter_type'] = On_base_ratio_4vs1

# 조건 1에 해당하는 행에 'On_base_ratio_0vs2' 값을 할당
df_new.loc[(df_new['Pitcher_Cluster_Label'] == 4) & (df_new['Batter_Cluster_Label'] == 2), 'On_base_ratio_by_pitcher_batter_type'] = On_base_ratio_4vs2

# 조건 2에 해당하는 행에 'On_base_ratio_0vs3' 값을 할당
df_new.loc[(df_new['Pitcher_Cluster_Label'] == 4) & (df_new['Batter_Cluster_Label'] == 3), 'On_base_ratio_by_pitcher_batter_type'] = On_base_ratio_4vs3

# 조건 2에 해당하는 행에 'On_base_ratio_0vs3' 값을 할당
df_new.loc[(df_new['Pitcher_Cluster_Label'] == 4) & (df_new['Batter_Cluster_Label'] == 4), 'On_base_ratio_by_pitcher_batter_type'] = On_base_ratio_4vs4

# 조건 1에 해당하는 행에 'On_base_ratio_0vs0' 값을 할당
df_new.loc[(df_new['Pitcher_Cluster_Label'] == 5) & (df_new['Batter_Cluster_Label'] == 0), 'On_base_ratio_by_pitcher_batter_type'] = On_base_ratio_5vs0

# 조건 2에 해당하는 행에 'On_base_ratio_0vs1' 값을 할당
df_new.loc[(df_new['Pitcher_Cluster_Label'] == 5) & (df_new['Batter_Cluster_Label'] == 1), 'On_base_ratio_by_pitcher_batter_type'] = On_base_ratio_5vs1

# 조건 1에 해당하는 행에 'On_base_ratio_0vs2' 값을 할당
df_new.loc[(df_new['Pitcher_Cluster_Label'] == 5) & (df_new['Batter_Cluster_Label'] == 2), 'On_base_ratio_by_pitcher_batter_type'] = On_base_ratio_5vs2

# 조건 2에 해당하는 행에 'On_base_ratio_0vs3' 값을 할당
df_new.loc[(df_new['Pitcher_Cluster_Label'] == 5) & (df_new['Batter_Cluster_Label'] == 3), 'On_base_ratio_by_pitcher_batter_type'] = On_base_ratio_5vs3

# 조건 2에 해당하는 행에 'On_base_ratio_0vs3' 값을 할당
df_new.loc[(df_new['Pitcher_Cluster_Label'] == 5) & (df_new['Batter_Cluster_Label'] == 4), 'On_base_ratio_by_pitcher_batter_type'] = On_base_ratio_5vs4

In [481]:
df_new['On_base_ratio_by_pitcher_batter_type'] = df_new['On_base_ratio_by_pitcher_batter_type'].astype(float)
df_new['zone'] = df_new['zone'].astype(int)
df_new['pitch_type'] = df_new['pitch_type'].astype(int)

In [482]:
df_new.head()

pitch_type  release_speed  release_pos_x  release_pos_z  zone stand  \
0           2           84.6          -2.20           6.49     9   1.0   
1           3           85.7          -2.20           6.43    13   1.0   
2           3           92.1          -2.28           6.39     8   1.0   
3           1           91.9          -1.28           6.59     4   1.0   
4           1           94.6          -1.86           6.23     7   1.0   

  p_throws  balls  strikes  pfx_x  pfx_z  plate_x  plate_z  outs_when_up  \
0      1.0      0        2   0.47   0.25     0.60     1.68             2   
1      1.0      1        2  -1.12   0.61    -0.82     1.46             1   
2      1.0      0        1  -1.17   1.18    -0.15     2.02             2   
3      1.0      1        1  -0.50   1.67    -0.29     2.84             2   
4      1.0      3        2  -0.42   1.74    -0.40     2.09             0   

   inning  release_spin_rate  release_extension  release_pos_y  at_bat_number  \
0       5             2299.0                6.8          53.74             45   
1       3             1647.0                6.9          53.65             28   
2       1             2233.0                6.6          53.87              9   
3       4             2300.0                6.8          53.68             28   
4       3             2330.0                6.8          53.66             16   

   pitch_number  spin_axis  on_3b  on_2b  on_1b  bat_score  fld_score  \
0             3      112.0      0      1      1          1          3   
1             5      221.0      0      0      1          1          1   
2             2      207.0      0      0      0          0          1   
3             3      194.0      0      1      1          0          0   
4             6      205.0      0      0      0          0          0   

   Pitcher_Cluster_Label  Batter_Cluster_Label events  \
0                      5                     1      0   
1                      5                     1      0   
2                      5                     1      1   
3                      5                     1      1   
4                      5                     1      0   

   On_base_ratio_by_pitcher_batter_type  
0                              0.432034  
1                              0.432034  
2                              0.432034  
3                              0.432034  
4                              0.432034

In [483]:
df_new.tail(10)

pitch_type  release_speed  release_pos_x  release_pos_z  zone  \
550594           1      93.560787      -1.230770       6.317636     4   
550595           1      94.266397      -2.298545       5.355202    11   
550596           1      94.331172      -2.371482       5.568755     9   
550597           1      97.897861      -1.485080       6.091230    12   
550598           1      95.045397      -2.208123       6.071092     1   
550599           1      96.414908      -1.338895       5.924706     6   
550600           1      90.572849       1.692510       6.050082     5   
550601           1      89.528436       1.871257       5.831956     5   
550602           2      84.091127      -1.240549       5.681648     8   
550603           2      78.899439       0.935028       5.991676    12   

           stand p_throws  balls  strikes     pfx_x     pfx_z   plate_x  \
550594       1.0      1.0      2        2 -0.944953  1.245910 -0.414446   
550595       1.0      1.0      0        1 -1.329757  0.858482 -1.838949   
550596       2.0      1.0      3        2 -0.684897  1.446409 -0.488076   
550597  1.074866      1.0      0        1 -0.708717  1.436524  0.235722   
550598  1.648466      1.0      1        1 -0.948533  0.859111 -0.168190   
550599  1.370183      1.0      1        0 -0.691491  1.283316  0.397018   
550600       1.0      2.0      0        0  0.327654  1.431773 -0.307244   
550601       1.0      2.0      0        0  1.286300  0.551194  0.176850   
550602       1.0      1.0      2        1  0.560211 -0.455014  0.219282   
550603       1.0      2.0      3        2 -0.840671 -1.387207 -0.900110   

         plate_z  outs_when_up  inning  release_spin_rate  release_extension  \
550594  2.436079             0       1        2218.956850           6.463790   
550595  3.996559             1       3        2242.495957           6.516801   
550596  2.439886             0       8        2296.436213           6.279527   
550597  3.722567             2       2        2482.224599           6.114973   
550598  3.045153             0       4        2204.593863           5.840614   
550599  2.508996             0       8        2269.000000           6.340872   
550600  2.161024             2       3        2451.502048           6.000410   
550601  2.427675             1       3        1733.513744           6.057188   
550602  1.936887             1       7        2554.991549           6.796620   
550603  0.160171             0       1        2720.888265           6.077653   

        release_pos_y  at_bat_number  pitch_number   spin_axis  on_3b  on_2b  \
550594      54.011426              9             5  217.000000      0      0   
550595      54.006559             22             3  212.831986      0      0   
550596      54.241245             69             6  216.000000      0      0   
550597      54.363529             17             3  208.224599      0      0   
550598      54.648294             32             3  209.945397      0      0   
550599      54.131725             70             2  216.110550      0      0   
550600      54.534570             29             1  150.753073      0      0   
550601      54.479387             17             1  138.315008      0      0   
550602      53.673507             51             5   51.987324      0      0   
550603      54.402347              2             6  328.385458      0      0   

        on_1b  bat_score  fld_score  Pitcher_Cluster_Label  \
550594      1          0          1                      0   
550595      0          0          2                      3   
550596      0          7          3                      1   
550597      0          2          1                      1   
550598      1          2          3                      1   
550599      0          7          2                      2   
550600      0          1          4                      4   
550601      0          0          0                      1   
550602      0          0          4                      1

## 최종 변수:
X = df_new[['pitch_type', 'release_speed', 'release_pos_x', 'release_pos_z', 'zone', 'stand', 'p_throws', 'balls', 'strikes', 'pfx_x', 'pfx_z', 'plate_x', 'plate_z', 'outs_when_up', 'inning', 'release_spin_rate', 'release_extension', 'at_bat_number', 'pitch_number','bat_score','fld_score','on_3b','on_2b','on_1b','Pitcher_Cluster_Label','Batter_Cluster_Label','On_base_ratio_by_pitcher_batter_type']]

X = df_new[['pitch_type', 'release_speed', 'release_pos_x', 'release_pos_z', 'zone', 'stand', 'p_throws', 'balls', 'strikes', 'pfx_x', 'pfx_z', 'plate_x', 'plate_z', 'outs_when_up', 'inning', 'release_spin_rate', 'release_extension', 'at_bat_number', 'pitch_number','bat_score','fld_score','on_3b','on_2b','on_1b','Pitcher_Cluster_Label','Batter_Cluster_Label','On_base_ratio_by_pitcher_batter_type']]


In [484]:
# categorical_cols = ['pitch_type', 'zone', 'stand', 'p_throws', 'on_3b', 'on_2b', 'on_1b','Pitcher_Cluster_Label','Batter_Cluster_Label']


categorical_cols = ['pitch_type', 'zone', 'stand', 'p_throws', 'on_3b', 'on_2b', 'on_1b']

In [485]:
df_new.dtypes

pitch_type                                int64
release_speed                           float64
release_pos_x                           float64
release_pos_z                           float64
zone                                      int64
stand                                    object
p_throws                                 object
balls                                     int64
strikes                                   int64
pfx_x                                   float64
pfx_z                                   float64
plate_x                                 float64
plate_z                                 float64
outs_when_up                              int64
inning                                    int64
release_spin_rate                       float64
release_extension                       float64
release_pos_y                           float64
at_bat_number                             int64
pitch_number                              int64
spin_axis                               

In [486]:
# Assuming df_new is your DataFrame
print(df_new[(df_new['Pitcher_Cluster_Label'] == 0) & (df_new['Batter_Cluster_Label'] == 0)]['On_base_ratio_by_pitcher_batter_type'].head(1))
print(df_new[(df_new['Pitcher_Cluster_Label'] == 0) & (df_new['Batter_Cluster_Label'] == 1)]['On_base_ratio_by_pitcher_batter_type'].head(1))
print(df_new[(df_new['Pitcher_Cluster_Label'] == 0) & (df_new['Batter_Cluster_Label'] == 2)]['On_base_ratio_by_pitcher_batter_type'].head(1))
print(df_new[(df_new['Pitcher_Cluster_Label'] == 0) & (df_new['Batter_Cluster_Label'] == 3)]['On_base_ratio_by_pitcher_batter_type'].head(1))
print(df_new[(df_new['Pitcher_Cluster_Label'] == 0) & (df_new['Batter_Cluster_Label'] == 4)]['On_base_ratio_by_pitcher_batter_type'].head(1))


1483    0.429305
Name: On_base_ratio_by_pitcher_batter_type, dtype: float64
1473    0.414402
Name: On_base_ratio_by_pitcher_batter_type, dtype: float64
1488    0.460124
Name: On_base_ratio_by_pitcher_batter_type, dtype: float64
7207    0.116203
Name: On_base_ratio_by_pitcher_batter_type, dtype: float64
1482    0.31614
Name: On_base_ratio_by_pitcher_batter_type, dtype: float64


In [487]:
# Assuming df_new is your DataFrame
print(df_new[(df_new['Pitcher_Cluster_Label'] == 1) & (df_new['Batter_Cluster_Label'] == 0)]['On_base_ratio_by_pitcher_batter_type'].head(1))
print(df_new[(df_new['Pitcher_Cluster_Label'] == 1) & (df_new['Batter_Cluster_Label'] == 1)]['On_base_ratio_by_pitcher_batter_type'].head(1))
print(df_new[(df_new['Pitcher_Cluster_Label'] == 1) & (df_new['Batter_Cluster_Label'] == 2)]['On_base_ratio_by_pitcher_batter_type'].head(1))
print(df_new[(df_new['Pitcher_Cluster_Label'] == 1) & (df_new['Batter_Cluster_Label'] == 3)]['On_base_ratio_by_pitcher_batter_type'].head(1))
print(df_new[(df_new['Pitcher_Cluster_Label'] == 1) & (df_new['Batter_Cluster_Label'] == 4)]['On_base_ratio_by_pitcher_batter_type'].head(1))


2936    0.470058
Name: On_base_ratio_by_pitcher_batter_type, dtype: float64
2932    0.446039
Name: On_base_ratio_by_pitcher_batter_type, dtype: float64
2940    0.429932
Name: On_base_ratio_by_pitcher_batter_type, dtype: float64
3449    0.121043
Name: On_base_ratio_by_pitcher_batter_type, dtype: float64
2935    0.296188
Name: On_base_ratio_by_pitcher_batter_type, dtype: float64


In [488]:
# Assuming df_new is your DataFrame
print(df_new[(df_new['Pitcher_Cluster_Label'] == 2) & (df_new['Batter_Cluster_Label'] == 0)]['On_base_ratio_by_pitcher_batter_type'].head(1))
print(df_new[(df_new['Pitcher_Cluster_Label'] == 2) & (df_new['Batter_Cluster_Label'] == 1)]['On_base_ratio_by_pitcher_batter_type'].head(1))
print(df_new[(df_new['Pitcher_Cluster_Label'] == 2) & (df_new['Batter_Cluster_Label'] == 2)]['On_base_ratio_by_pitcher_batter_type'].head(1))
print(df_new[(df_new['Pitcher_Cluster_Label'] == 2) & (df_new['Batter_Cluster_Label'] == 3)]['On_base_ratio_by_pitcher_batter_type'].head(1))
print(df_new[(df_new['Pitcher_Cluster_Label'] == 2) & (df_new['Batter_Cluster_Label'] == 4)]['On_base_ratio_by_pitcher_batter_type'].head(1))


2665    0.475855
Name: On_base_ratio_by_pitcher_batter_type, dtype: float64
2659    0.441311
Name: On_base_ratio_by_pitcher_batter_type, dtype: float64
2669    0.427914
Name: On_base_ratio_by_pitcher_batter_type, dtype: float64
6603    0.130597
Name: On_base_ratio_by_pitcher_batter_type, dtype: float64
2674    0.303477
Name: On_base_ratio_by_pitcher_batter_type, dtype: float64


In [489]:
# Assuming df_new is your DataFrame
print(df_new[(df_new['Pitcher_Cluster_Label'] == 3) & (df_new['Batter_Cluster_Label'] == 0)]['On_base_ratio_by_pitcher_batter_type'].head(1))
print(df_new[(df_new['Pitcher_Cluster_Label'] == 3) & (df_new['Batter_Cluster_Label'] == 1)]['On_base_ratio_by_pitcher_batter_type'].head(1))
print(df_new[(df_new['Pitcher_Cluster_Label'] == 3) & (df_new['Batter_Cluster_Label'] == 2)]['On_base_ratio_by_pitcher_batter_type'].head(1))
print(df_new[(df_new['Pitcher_Cluster_Label'] == 3) & (df_new['Batter_Cluster_Label'] == 3)]['On_base_ratio_by_pitcher_batter_type'].head(1))
print(df_new[(df_new['Pitcher_Cluster_Label'] == 3) & (df_new['Batter_Cluster_Label'] == 4)]['On_base_ratio_by_pitcher_batter_type'].head(1))


4719    0.31877
Name: On_base_ratio_by_pitcher_batter_type, dtype: float64
4705    0.291951
Name: On_base_ratio_by_pitcher_batter_type, dtype: float64
4711    0.438691
Name: On_base_ratio_by_pitcher_batter_type, dtype: float64
7469    0.076262
Name: On_base_ratio_by_pitcher_batter_type, dtype: float64
4709    0.357143
Name: On_base_ratio_by_pitcher_batter_type, dtype: float64


In [490]:
# Assuming df_new is your DataFrame
print(df_new[(df_new['Pitcher_Cluster_Label'] == 4) & (df_new['Batter_Cluster_Label'] == 0)]['On_base_ratio_by_pitcher_batter_type'].head(1))
print(df_new[(df_new['Pitcher_Cluster_Label'] == 4) & (df_new['Batter_Cluster_Label'] == 1)]['On_base_ratio_by_pitcher_batter_type'].head(1))
print(df_new[(df_new['Pitcher_Cluster_Label'] == 4) & (df_new['Batter_Cluster_Label'] == 2)]['On_base_ratio_by_pitcher_batter_type'].head(1))
print(df_new[(df_new['Pitcher_Cluster_Label'] == 4) & (df_new['Batter_Cluster_Label'] == 3)]['On_base_ratio_by_pitcher_batter_type'].head(1))
print(df_new[(df_new['Pitcher_Cluster_Label'] == 4) & (df_new['Batter_Cluster_Label'] == 4)]['On_base_ratio_by_pitcher_batter_type'].head(1))


1762    0.441994
Name: On_base_ratio_by_pitcher_batter_type, dtype: float64
1730    0.406092
Name: On_base_ratio_by_pitcher_batter_type, dtype: float64
1747    0.442132
Name: On_base_ratio_by_pitcher_batter_type, dtype: float64
22268    0.104334
Name: On_base_ratio_by_pitcher_batter_type, dtype: float64
1739    0.294199
Name: On_base_ratio_by_pitcher_batter_type, dtype: float64


In [491]:
# Assuming df_new is your DataFrame
print(df_new[(df_new['Pitcher_Cluster_Label'] == 5) & (df_new['Batter_Cluster_Label'] == 0)]['On_base_ratio_by_pitcher_batter_type'].head(1))
print(df_new[(df_new['Pitcher_Cluster_Label'] == 5) & (df_new['Batter_Cluster_Label'] == 1)]['On_base_ratio_by_pitcher_batter_type'].head(1))
print(df_new[(df_new['Pitcher_Cluster_Label'] == 5) & (df_new['Batter_Cluster_Label'] == 2)]['On_base_ratio_by_pitcher_batter_type'].head(1))
print(df_new[(df_new['Pitcher_Cluster_Label'] == 5) & (df_new['Batter_Cluster_Label'] == 3)]['On_base_ratio_by_pitcher_batter_type'].head(1))
print(df_new[(df_new['Pitcher_Cluster_Label'] == 5) & (df_new['Batter_Cluster_Label'] == 4)]['On_base_ratio_by_pitcher_batter_type'].head(1))


23    0.391079
Name: On_base_ratio_by_pitcher_batter_type, dtype: float64
0    0.432034
Name: On_base_ratio_by_pitcher_batter_type, dtype: float64
33    0.354038
Name: On_base_ratio_by_pitcher_batter_type, dtype: float64
4318    0.292683
Name: On_base_ratio_by_pitcher_batter_type, dtype: float64
17    0.274489
Name: On_base_ratio_by_pitcher_batter_type, dtype: float64


# Catboost

In [492]:
# pip install mlxtend

In [493]:
df_new.head()

pitch_type  release_speed  release_pos_x  release_pos_z  zone stand  \
0           2           84.6          -2.20           6.49     9   1.0   
1           3           85.7          -2.20           6.43    13   1.0   
2           3           92.1          -2.28           6.39     8   1.0   
3           1           91.9          -1.28           6.59     4   1.0   
4           1           94.6          -1.86           6.23     7   1.0   

  p_throws  balls  strikes  pfx_x  pfx_z  plate_x  plate_z  outs_when_up  \
0      1.0      0        2   0.47   0.25     0.60     1.68             2   
1      1.0      1        2  -1.12   0.61    -0.82     1.46             1   
2      1.0      0        1  -1.17   1.18    -0.15     2.02             2   
3      1.0      1        1  -0.50   1.67    -0.29     2.84             2   
4      1.0      3        2  -0.42   1.74    -0.40     2.09             0   

   inning  release_spin_rate  release_extension  release_pos_y  at_bat_number  \
0       5             2299.0                6.8          53.74             45   
1       3             1647.0                6.9          53.65             28   
2       1             2233.0                6.6          53.87              9   
3       4             2300.0                6.8          53.68             28   
4       3             2330.0                6.8          53.66             16   

   pitch_number  spin_axis  on_3b  on_2b  on_1b  bat_score  fld_score  \
0             3      112.0      0      1      1          1          3   
1             5      221.0      0      0      1          1          1   
2             2      207.0      0      0      0          0          1   
3             3      194.0      0      1      1          0          0   
4             6      205.0      0      0      0          0          0   

   Pitcher_Cluster_Label  Batter_Cluster_Label events  \
0                      5                     1      0   
1                      5                     1      0   
2                      5                     1      1   
3                      5                     1      1   
4                      5                     1      0   

   On_base_ratio_by_pitcher_batter_type  
0                              0.432034  
1                              0.432034  
2                              0.432034  
3                              0.432034  
4                              0.432034

In [494]:
df_new[categorical_cols] = df_new[categorical_cols].astype(int)


In [495]:
from sklearn.model_selection import train_test_split

# 독립 변수와 종속 변수로 데이터 나누기
X = df_new[['pitch_type', 'release_speed', 'release_pos_x', 'release_pos_z', 'zone',
       'stand', 'p_throws', 'balls', 'strikes', 'pfx_x', 'pfx_z', 'plate_x',
       'plate_z', 'outs_when_up', 'inning', 'release_spin_rate',
       'release_extension', 'release_pos_y', 'at_bat_number', 'pitch_number',
       'spin_axis', 'on_3b', 'on_2b', 'on_1b', 'bat_score', 'fld_score',
       'On_base_ratio_by_pitcher_batter_type']]

y = df_new['events']  # 종속 변수

# # train_test_split을 사용하여 데이터 분할 (예시로 테스트 데이터를 20%로 설정)
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)


In [496]:
catboost_params = {
    'random_strength': 1.0,
    'learning_rate': 0.1,
    'l2_leaf_reg': 1
}


In [497]:
from catboost import CatBoostClassifier
best_model_catboost = CatBoostClassifier(verbose=50,cat_features=categorical_cols, **catboost_params)


In [498]:
best_model_catboost.fit(X_train, y_train)

0:	learn: 0.6665124	total: 217ms	remaining: 3m 36s
50:	learn: 0.4544284	total: 10s	remaining: 3m 6s
100:	learn: 0.4199458	total: 21.3s	remaining: 3m 9s
150:	learn: 0.4038981	total: 29.9s	remaining: 2m 47s
200:	learn: 0.3956418	total: 38.4s	remaining: 2m 32s
250:	learn: 0.3914584	total: 47.1s	remaining: 2m 20s
300:	learn: 0.3892627	total: 55.9s	remaining: 2m 9s
350:	learn: 0.3874757	total: 1m 4s	remaining: 1m 59s
400:	learn: 0.3843166	total: 1m 13s	remaining: 1m 49s
450:	learn: 0.3831299	total: 1m 22s	remaining: 1m 39s
500:	learn: 0.3818935	total: 1m 30s	remaining: 1m 30s
550:	learn: 0.3805934	total: 1m 41s	remaining: 1m 22s
600:	learn: 0.3794198	total: 1m 49s	remaining: 1m 12s
650:	learn: 0.3782496	total: 1m 58s	remaining: 1m 3s
700:	learn: 0.3772090	total: 2m 7s	remaining: 54.2s
750:	learn: 0.3760538	total: 2m 15s	remaining: 45s
800:	learn: 0.3750386	total: 2m 24s	remaining: 36s
850:	learn: 0.3739444	total: 2m 33s	remaining: 26.9s
900:	learn: 0.3729175	total: 2m 42s	remaining: 17.8s
9

In [499]:
y_pred = best_model_catboost.predict(X_test)


In [500]:
from sklearn.metrics import accuracy_score, classification_report
accuracy = accuracy_score(y_test, y_pred)

# Display model performance metrics
print("모델 성능:")
print("정확도:", accuracy)
print("\n분류 보고서:")
print(classification_report(y_test, y_pred))

모델 성능:
정확도: 0.8156936460802209

분류 보고서:
              precision    recall  f1-score   support

           0       0.74      0.97      0.84     55024
           1       0.95      0.66      0.78     55097

    accuracy                           0.82    110121
   macro avg       0.85      0.82      0.81    110121
weighted avg       0.85      0.82      0.81    110121



In [246]:
from sklearn.model_selection import KFold, cross_val_score
from catboost import CatBoostClassifier
from sklearn.metrics import accuracy_score, classification_report

# Define the number of folds for k-fold cross-validation
num_folds = 5

# Initialize the CatBoostClassifier with your parameters
catboost_params = {
    'random_strength': 1.0,
    'learning_rate': 0.1,
    'l2_leaf_reg': 1
}
best_model_catboost = CatBoostClassifier(verbose=50, cat_features=categorical_cols, **catboost_params)

# Perform k-fold cross-validation
kfold = KFold(n_splits=num_folds, shuffle=True, random_state=42)
accuracy_scores = cross_val_score(best_model_catboost, X, y, cv=kfold, scoring='accuracy')

# Display the accuracy scores for each fold
print("각 Fold의 정확도:", accuracy_scores)
print("평균 정확도:", accuracy_scores.mean())

# Optionally, train the model on the entire dataset
best_model_catboost.fit(X, y)


0:	learn: 0.6665070	total: 345ms	remaining: 5m 45s
50:	learn: 0.4496247	total: 9.51s	remaining: 2m 57s
100:	learn: 0.4198654	total: 19.6s	remaining: 2m 54s
150:	learn: 0.4056619	total: 28.2s	remaining: 2m 38s
200:	learn: 0.3972715	total: 37.1s	remaining: 2m 27s
250:	learn: 0.3921903	total: 45.7s	remaining: 2m 16s
300:	learn: 0.3893654	total: 54.3s	remaining: 2m 6s
350:	learn: 0.3877622	total: 1m 3s	remaining: 1m 57s
400:	learn: 0.3856130	total: 1m 13s	remaining: 1m 49s
450:	learn: 0.3842016	total: 1m 28s	remaining: 1m 47s
500:	learn: 0.3829353	total: 1m 41s	remaining: 1m 41s
550:	learn: 0.3817766	total: 1m 53s	remaining: 1m 32s
600:	learn: 0.3806760	total: 2m 4s	remaining: 1m 22s
650:	learn: 0.3795248	total: 2m 14s	remaining: 1m 12s
700:	learn: 0.3782551	total: 2m 23s	remaining: 1m 1s
750:	learn: 0.3770602	total: 2m 33s	remaining: 51s
800:	learn: 0.3755421	total: 2m 43s	remaining: 40.5s
850:	learn: 0.3745471	total: 2m 53s	remaining: 30.3s
900:	learn: 0.3732876	total: 3m 1s	remaining: 2

In [501]:
from sklearn.model_selection import RandomizedSearchCV
from catboost import CatBoostClassifier

# CatBoostClassifier 객체 생성
catboost = CatBoostClassifier(cat_features=categorical_cols, verbose=50)

# 탐색할 하이퍼파라미터 공간 정의
param_distributions = {
    'random_strength': [0.1, 0.5, 1.0],
    'learning_rate': [0.01, 0.05, 0.1, 0.2],
    'l2_leaf_reg': [0.1, 0.5, 1, 3, 5]
}

# RandomizedSearchCV를 사용하여 최적의 하이퍼파라미터 탐색
random_search = RandomizedSearchCV(catboost, param_distributions, cv=5, n_iter=10, scoring='accuracy', random_state=42)
random_search.fit(X_train, y_train)

# 최적의 하이퍼파라미터 출력
print("최적의 하이퍼파라미터:", random_search.best_params_)

# 최적의 모델
best_model = random_search.best_estimator_

# 테스트 데이터로 모델 평가
y_pred = best_model.predict(X_test)
accuracy = accuracy_score(y_test, y_pred)

# 모델 성능 출력
print("\n모델 성능:")
print("정확도:", accuracy)
print("\n분류 보고서:")
print(classification_report(y_test, y_pred))


0:	learn: 0.6901110	total: 221ms	remaining: 3m 40s
50:	learn: 0.6101327	total: 9.11s	remaining: 2m 49s
100:	learn: 0.5783677	total: 16.6s	remaining: 2m 27s
150:	learn: 0.5582468	total: 23.8s	remaining: 2m 13s
200:	learn: 0.5277705	total: 30.8s	remaining: 2m 2s
250:	learn: 0.5087961	total: 41.3s	remaining: 2m 3s
300:	learn: 0.4954371	total: 50.4s	remaining: 1m 57s
350:	learn: 0.4854632	total: 59s	remaining: 1m 49s
400:	learn: 0.4752686	total: 1m 6s	remaining: 1m 38s
450:	learn: 0.4642158	total: 1m 12s	remaining: 1m 28s
500:	learn: 0.4590084	total: 1m 19s	remaining: 1m 19s
550:	learn: 0.4539636	total: 1m 25s	remaining: 1m 10s
600:	learn: 0.4468278	total: 1m 32s	remaining: 1m 1s
650:	learn: 0.4439200	total: 1m 38s	remaining: 53.1s
700:	learn: 0.4404907	total: 1m 45s	remaining: 45s
750:	learn: 0.4356774	total: 1m 52s	remaining: 37.2s
800:	learn: 0.4316228	total: 1m 58s	remaining: 29.5s
850:	learn: 0.4281520	total: 2m 6s	remaining: 22.1s
900:	learn: 0.4244929	total: 2m 14s	remaining: 14.8s


KeyboardInterrupt: 

# LGBM

In [502]:
# X = df_new[['pitch_type', 'release_speed', 'release_pos_x', 'release_pos_z', 'zone', 'stand', 'p_throws', 'balls', 'strikes', 'pfx_x', 'pfx_z', 'plate_x', 'plate_z', 'outs_when_up', 'inning', 'release_spin_rate', 'release_extension', 'at_bat_number', 'pitch_number', 'bat_score', 'fld_score', 'on_3b', 'on_2b', 'on_1b', 'Pitcher_Cluster_Label', 'Batter_Cluster_Label', 'On_base_ratio_by_pitcher_batter_type']]
# y = df_new['events']



# # 변경된 코드
# X = df_new[['pitch_type', 'release_speed', 'release_pos_x', 'release_pos_z', 'zone', 'stand', 'p_throws', 'balls', 'strikes', 'pfx_x', 'pfx_z', 'plate_x', 'plate_z', 'outs_when_up', 'inning', 'release_spin_rate', 'release_extension', 'release_pos_y', 'at_bat_number', 'pitch_number', 'spin_axis','bat_score','fld_score','on_3b','on_2b','on_1b','Pitcher_Cluster_Label', 'Batter_Cluster_Label','On_base_ratio_by_pitcher_batter_type']]
# y = df_new['events']

# # 변경된 코드
# X = df_new[['pitch_type', 'release_speed', 'release_pos_x', 'release_pos_z', 'zone', 'stand', 'p_throws', 'balls', 'strikes', 'pfx_x', 'pfx_z', 'plate_x', 'plate_z', 'outs_when_up', 'inning', 'release_spin_rate', 'release_extension', 'release_pos_y', 'at_bat_number', 'pitch_number', 'spin_axis','bat_score','fld_score','on_3b','on_2b','on_1b','On_base_ratio_by_pitcher_batter_type']]
# y = df_new['events']

X = df_new[['pitch_type', 'release_speed', 'release_pos_x', 'release_pos_z', 'zone',
       'stand', 'p_throws', 'balls', 'strikes', 'pfx_x', 'pfx_z', 'plate_x',
       'plate_z', 'outs_when_up', 'inning', 'release_spin_rate',
       'release_extension', 'release_pos_y', 'at_bat_number', 'pitch_number',
       'spin_axis', 'on_3b', 'on_2b', 'on_1b', 'bat_score', 'fld_score',
       'On_base_ratio_by_pitcher_batter_type']]

y = df_new['events'] 

In [503]:
cat_features = ['pitch_type', 'zone', 'stand', 'p_throws', 'on_3b', 'on_2b', 'on_1b']
for i in enumerate (cat_features) :
    ca = i[1]
    X[ca] = X[ca].astype('category')

/var/folders/r1/znzmlx_d1xg065b8mc9v3v7r0000gn/T/ipykernel_24001/2170398262.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  X[ca] = X[ca].astype('category')


In [504]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

In [505]:
# pip install --upgrade matplotlib


In [506]:
# First Trial : 
params = {'subsample': 0.5, 'num_leaves': 65, 'n_estimators': 300, 'max_depth': 13, 'learning_rate': 0.1, 'colsample_bytree': 0.5, 'boosting_type': 'gbdt'}

In [507]:
import lightgbm as lgb

best_model_lgbm = lgb.LGBMClassifier(**params)

In [508]:
best_model_lgbm.fit(X_train, y_train)

[LightGBM] [Info] Number of positive: 220205, number of negative: 220278
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.014169 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 3078
[LightGBM] [Info] Number of data points in the train set: 440483, number of used features: 27
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.499917 -> initscore=-0.000331
[LightGBM] [Info] Start training from score -0.000331


LGBMClassifier(colsample_bytree=0.5, max_depth=13, n_estimators=300,
               num_leaves=65, subsample=0.5)

In [509]:
y_pred = best_model_lgbm.predict(X_test)

In [172]:
accuracy = accuracy_score(y_test, y_pred)

# Display model performance metrics
print("모델 성능:")
print("정확도:", accuracy)
print("\n분류 보고서:")
print(classification_report(y_test, y_pred))

모델 성능:
정확도: 0.8162657440451867

분류 보고서:
              precision    recall  f1-score   support

           0       0.74      0.96      0.84     55024
           1       0.95      0.67      0.78     55097

    accuracy                           0.82    110121
   macro avg       0.85      0.82      0.81    110121
weighted avg       0.85      0.82      0.81    110121



In [510]:
from sklearn.model_selection import RandomizedSearchCV
import lightgbm as lgb
from scipy.stats import randint as sp_randint

# Define the parameters and their ranges for searching
param_dist = {
    'num_leaves': sp_randint(6, 65),
    'max_depth': sp_randint(3, 15),
    'learning_rate': [0.05, 0.1, 0.2 ],
    'n_estimators': [500],
    'subsample': [0.5, 0.6],
    'colsample_bytree': [0.5, 0.6]
    # Add other parameters you want to tune here
}

# Create a base LGBM model
base_model = lgb.LGBMClassifier()

# Create RandomizedSearchCV object
random_search = RandomizedSearchCV(
    estimator=base_model,
    param_distributions=param_dist,
    n_iter=100,  # Adjust the number of iterations as needed
    scoring='accuracy',  # Choose an appropriate scoring metric
    cv=5,  # Number of cross-validation folds
    verbose=1,
    n_jobs=-1,  # Use all available cores
    random_state=42
)

# Fit the RandomizedSearchCV object to the data
random_search.fit(X_train, y_train)

# Print the best parameters found
print("최적의 하이퍼파라미터:", random_search.best_params_)

# Get the best model from RandomizedSearchCV
best_model = random_search.best_estimator_

# Predict using the best model
y_pred = best_model.predict(X_test)

# Calculate accuracy
accuracy = accuracy_score(y_test, y_pred)

# Display model performance metrics
print("모델 성능:")
print("정확도:", accuracy)
print("\n분류 보고서:")
print(classification_report(y_test, y_pred))


Fitting 5 folds for each of 100 candidates, totalling 500 fits
[LightGBM] [Info] Number of positive: 176164, number of negative: 176222
[LightGBM] [Info] Number of positive: 176164, number of negative: 176223
[LightGBM] [Info] Number of positive: 176164, number of negative: 176223
[LightGBM] [Info] Number of positive: 176164, number of negative: 176222
[LightGBM] [Info] Number of positive: 176164, number of negative: 176222
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.119685 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 3080
[LightGBM] [Info] Number of data points in the train set: 352386, number of used features: 27
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.499918 -> initscore=-0.000329
[LightGBM] [Info] Start training from score -0.000329
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing wa

In [268]:
import lightgbm as lgb
from sklearn.model_selection import KFold, cross_val_score
from sklearn.metrics import accuracy_score, classification_report

X = df_new[['pitch_type', 'release_speed', 'release_pos_x', 'release_pos_z', 'zone',
            'stand', 'p_throws', 'balls', 'strikes', 'pfx_x', 'pfx_z', 'plate_x',
            'plate_z', 'outs_when_up', 'inning', 'release_spin_rate',
            'release_extension', 'release_pos_y', 'at_bat_number', 'pitch_number',
            'spin_axis', 'on_3b', 'on_2b', 'on_1b', 'bat_score', 'fld_score',
            'On_base_ratio_by_pitcher_batter_type']]
y = df_new['events']

cat_features = ['pitch_type', 'zone', 'stand', 'p_throws', 'on_3b', 'on_2b', 'on_1b']
for feature in cat_features:
    X[feature] = X[feature].astype('category')

params = {'subsample': 0.5, 'num_leaves': 65, 'n_estimators': 300, 'max_depth': 13, 'learning_rate': 0.1, 'colsample_bytree': 0.5, 'boosting_type': 'gbdt'}
# params = {'random_strength': 1.0, 'depth': 6, 'learning_rate':0.1, 'iterations':500, 'l2_leaf_reg':1.0 }

# 
# 
# 
# 
# thread_count=None
# loss_function='Logloss'
# Initialize the LightGBM model
best_model_lgbm = lgb.LGBMClassifier(**params)

# Define the number of folds for k-fold cross-validation
num_folds = 10

# Perform k-fold cross-validation
kfold = KFold(n_splits=num_folds, shuffle=True, random_state=42)
accuracy_scores = cross_val_score(best_model_lgbm, X, y, cv=kfold, scoring='accuracy')

# Display the accuracy scores for each fold
print("각 Fold의 정확도:", accuracy_scores)
print("평균 정확도:", accuracy_scores.mean())

# Optionally, fit the model on the entire dataset
best_model_lgbm.fit(X, y)


/var/folders/r1/znzmlx_d1xg065b8mc9v3v7r0000gn/T/ipykernel_24001/2654727690.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  X[feature] = X[feature].astype('category')


[LightGBM] [Warning] Unknown parameter: iterations
[LightGBM] [Warning] Unknown parameter: random_strength
[LightGBM] [Warning] Unknown parameter: depth
[LightGBM] [Warning] Unknown parameter: l2_leaf_reg
[LightGBM] [Warning] Unknown parameter: iterations
[LightGBM] [Warning] Unknown parameter: random_strength
[LightGBM] [Warning] Unknown parameter: depth
[LightGBM] [Warning] Unknown parameter: l2_leaf_reg
[LightGBM] [Info] Number of positive: 247664, number of negative: 247879
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.054366 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 3076
[LightGBM] [Info] Number of data points in the train set: 495543, number of used features: 27
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.499783 -> initscore=-0.000868
[LightGBM] [Info] Start training from score -0.000868
[LightGBM] [Warning] Unknown 

LGBMClassifier(depth=6, iterations=500, l2_leaf_reg=1.0, random_strength=1.0)

# XGBoost

X = df_new[['pitch_type', 'release_speed', 'release_pos_x', 'release_pos_z', 'zone', 'stand', 'p_throws', 'balls', 'strikes', 'pfx_x', 'pfx_z', 'plate_x', 'plate_z', 'outs_when_up', 'inning', 'release_spin_rate', 'release_extension', 'at_bat_number', 'pitch_number','bat_score','fld_score','on_3b','on_2b','on_1b','Pitcher_Cluster_Label','Batter_Cluster_Label','On_base_ratio_by_pitcher_batter_type']]
y = df_new['events']

In [511]:
# X = df_new[['pitch_type', 'release_speed', 'release_pos_x', 'release_pos_z', 'zone', 'stand', 'p_throws', 'balls', 'strikes', 'pfx_x', 'pfx_z', 'plate_x', 'plate_z', 'outs_when_up', 'inning', 'release_spin_rate', 'release_extension', 'at_bat_number', 'pitch_number','bat_score','fld_score','on_3b','on_2b','on_1b','Pitcher_Cluster_Label','Batter_Cluster_Label','On_base_ratio_by_pitcher_batter_type']]
# y = df_new['events']

# # 변경된 코드
# X = df_new[['pitch_type', 'release_speed', 'release_pos_x', 'release_pos_z', 'zone', 'stand', 'p_throws', 'balls', 'strikes', 'pfx_x', 'pfx_z', 'plate_x', 'plate_z', 'outs_when_up', 'inning', 'release_spin_rate', 'release_extension', 'release_pos_y', 'at_bat_number', 'pitch_number', 'spin_axis','bat_score','fld_score','on_3b','on_2b','on_1b','Pitcher_Cluster_Label', 'Batter_Cluster_Label','On_base_ratio_by_pitcher_batter_type']]
# y = df_new['events']

# 변경된 코드
# X = df_new[['pitch_type', 'release_speed', 'release_pos_x', 'release_pos_z', 'zone', 'stand', 'p_throws', 'balls', 'strikes', 'pfx_x', 'pfx_z', 'plate_x', 'plate_z', 'outs_when_up', 'inning', 'release_spin_rate', 'release_extension', 'release_pos_y', 'at_bat_number', 'pitch_number', 'spin_axis','bat_score','fld_score','on_3b','on_2b','on_1b','On_base_ratio_by_pitcher_batter_type']]
# y = df_new['events']

X = df_new[['pitch_type', 'release_speed', 'release_pos_x', 'release_pos_z', 'zone',
       'stand', 'p_throws', 'balls', 'strikes', 'pfx_x', 'pfx_z', 'plate_x',
       'plate_z', 'outs_when_up', 'inning', 'release_spin_rate',
       'release_extension', 'release_pos_y', 'at_bat_number', 'pitch_number',
       'spin_axis', 'on_3b', 'on_2b', 'on_1b', 'bat_score', 'fld_score',
       'On_base_ratio_by_pitcher_batter_type']]

y = df_new['events'] 

In [512]:


y= y.astype(int)
print(y.info())

<class 'pandas.core.series.Series'>
RangeIndex: 550604 entries, 0 to 550603
Series name: events
Non-Null Count   Dtype
--------------   -----
550604 non-null  int64
dtypes: int64(1)
memory usage: 4.2 MB
None


In [513]:
for col in categorical_cols:
    X[col] = X[col].astype('category')

/var/folders/r1/znzmlx_d1xg065b8mc9v3v7r0000gn/T/ipykernel_24001/274434676.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  X[col] = X[col].astype('category')


In [514]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

In [257]:
params = {'subsample': 0.79, 'num_leaves': 128, 'n_estimators': 500, 'min_child_weight': 1, 'max_depth': 8, 'learning_rate': 0.05, 'colsample_bytree': 0.89, 'objective': 'binary:logistic'}

In [258]:
from xgboost import XGBClassifier
best_model_xgb = XGBClassifier(enable_categorical=True)
best_model_xgb.set_params(**params)

XGBClassifier(base_score=None, booster=None, callbacks=None,
              colsample_bylevel=None, colsample_bynode=None,
              colsample_bytree=0.89, device=None, early_stopping_rounds=None,
              enable_categorical=True, eval_metric=None, feature_types=None,
              gamma=None, grow_policy=None, importance_type=None,
              interaction_constraints=None, learning_rate=0.05, max_bin=None,
              max_cat_threshold=None, max_cat_to_onehot=None,
              max_delta_step=None, max_depth=8, max_leaves=None,
              min_child_weight=1, missing=nan, monotone_constraints=None,
              multi_strategy=None, n_estimators=500, n_jobs=None,
              num_leaves=128, num_parallel_tree=None, ...)

In [179]:
best_model_xgb.fit(X_train, y_train)

/Library/Frameworks/Python.framework/Versions/3.8/lib/python3.8/site-packages/xgboost/core.py:160: UserWarning: [18:03:32] WARNING: /Users/runner/work/xgboost/xgboost/src/learner.cc:742: 
Parameters: { "num_leaves" } are not used.

  warnings.warn(smsg, UserWarning)


XGBClassifier(base_score=None, booster=None, callbacks=None,
              colsample_bylevel=None, colsample_bynode=None,
              colsample_bytree=0.89, device=None, early_stopping_rounds=None,
              enable_categorical=True, eval_metric=None, feature_types=None,
              gamma=None, grow_policy=None, importance_type=None,
              interaction_constraints=None, learning_rate=0.05, max_bin=None,
              max_cat_threshold=None, max_cat_to_onehot=None,
              max_delta_step=None, max_depth=8, max_leaves=None,
              min_child_weight=1, missing=nan, monotone_constraints=None,
              multi_strategy=None, n_estimators=500, n_jobs=None,
              num_leaves=128, num_parallel_tree=None, ...)

In [180]:
y_pred = best_model_xgb.predict(X_test)

In [181]:
accuracy = accuracy_score(y_test, y_pred)
report = classification_report(y_test, y_pred)

print("정확도:", accuracy)
print("분류 보고서:\n", report)

정확도: 0.8123700293313718
분류 보고서:
               precision    recall  f1-score   support

           0       0.74      0.96      0.84     55024
           1       0.94      0.66      0.78     55097

    accuracy                           0.81    110121
   macro avg       0.84      0.81      0.81    110121
weighted avg       0.84      0.81      0.81    110121



In [515]:
from sklearn.model_selection import RandomizedSearchCV
from xgboost import XGBClassifier

# Define the parameter grid for RandomizedSearchCV
param_dist = {
    'n_estimators': [100, 300, 500],
    'max_depth': [3, 4, 5, 6, 8, 10, 12, 15],
    'learning_rate': [0.01, 0.05, 0.1, 0.15, 0.2],
    'subsample': [0.6, 0.7, 0.8, 0.9, 1.0],
    'colsample_bytree': [0.6, 0.7, 0.8, 0.9, 1.0],
    'min_child_weight': [1, 2, 3, 4]
    # Add other parameters you want to tune here
}

# Create a base XGBClassifier model
base_model = XGBClassifier(enable_categorical=True)

# Create RandomizedSearchCV object
random_search = RandomizedSearchCV(
    estimator=base_model,
    param_distributions=param_dist,
    n_iter=100,  # Adjust the number of iterations as needed
    scoring='accuracy',  # Choose an appropriate scoring metric
    cv=5,  # Number of cross-validation folds
    verbose=1,
    n_jobs=-1,  # Use all available cores
    random_state=42
)

# Fit the RandomizedSearchCV object to the data
random_search.fit(X_train, y_train)

# Print the best parameters found
print("최적의 하이퍼파라미터:", random_search.best_params_)

# Get the best model from RandomizedSearchCV
best_model = random_search.best_estimator_

# Predict using the best model
y_pred = best_model.predict(X_test)

# Calculate accuracy
accuracy = accuracy_score(y_test, y_pred)

# Display model performance metrics
print("모델 성능:")
print("정확도:", accuracy)
print("\n분류 보고서:")
print(classification_report(y_test, y_pred))


Fitting 5 folds for each of 100 candidates, totalling 500 fits
최적의 하이퍼파라미터: {'subsample': 0.9, 'n_estimators': 500, 'min_child_weight': 1, 'max_depth': 5, 'learning_rate': 0.2, 'colsample_bytree': 1.0}
모델 성능:
정확도: 0.8087739849801582

분류 보고서:
              precision    recall  f1-score   support

           0       0.74      0.95      0.83     55024
           1       0.93      0.67      0.78     55097

    accuracy                           0.81    110121
   macro avg       0.83      0.81      0.81    110121
weighted avg       0.83      0.81      0.81    110121



In [264]:
from xgboost import XGBClassifier
from sklearn.model_selection import KFold, cross_val_score
from sklearn.metrics import accuracy_score, classification_report

X = df_new[['pitch_type', 'release_speed', 'release_pos_x', 'release_pos_z', 'zone',
            'stand', 'p_throws', 'balls', 'strikes', 'pfx_x', 'pfx_z', 'plate_x',
            'plate_z', 'outs_when_up', 'inning', 'release_spin_rate',
            'release_extension', 'release_pos_y', 'at_bat_number', 'pitch_number',
            'spin_axis', 'on_3b', 'on_2b', 'on_1b', 'bat_score', 'fld_score',
            'On_base_ratio_by_pitcher_batter_type']]

y = df_new['events']
y = y.astype(int)

categorical_cols = ['pitch_type', 'zone', 'stand', 'p_throws', 'on_3b', 'on_2b', 'on_1b']

for col in categorical_cols:
    X[col] = X[col].astype('category')

params = {'subsample': 0.79, 'num_leaves': 128, 'n_estimators': 500, 'min_child_weight': 1, 'max_depth': 8, 'learning_rate': 0.05, 'colsample_bytree': 0.89, 'objective': 'binary:logistic'}

best_model_xgb = XGBClassifier(enable_categorical=True, **params)

# Define the number of folds for k-fold cross-validation
num_folds = 10

# Perform k-fold cross-validation
kfold = KFold(n_splits=num_folds, shuffle=True, random_state=42)
accuracy_scores = cross_val_score(best_model_xgb, X, y, cv=kfold, scoring='accuracy')

# Display the accuracy scores for each fold
print("각 Fold의 정확도:", accuracy_scores)
print("평균 정확도:", accuracy_scores.mean())

# Optionally, fit the model on the entire dataset
best_model_xgb.fit(X, y)


/var/folders/r1/znzmlx_d1xg065b8mc9v3v7r0000gn/T/ipykernel_24001/332972241.py:18: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  X[col] = X[col].astype('category')
/Library/Frameworks/Python.framework/Versions/3.8/lib/python3.8/site-packages/xgboost/core.py:160: UserWarning: [19:09:38] WARNING: /Users/runner/work/xgboost/xgboost/src/learner.cc:742: 
Parameters: { "num_leaves" } are not used.

  warnings.warn(smsg, UserWarning)
/Library/Frameworks/Python.framework/Versions/3.8/lib/python3.8/site-packages/xgboost/core.py:160: UserWarning: [19:09:56] WARNING: /Users/runner/work/xgboost/xgboost/src/learner.cc:742: 
Parameters: { "num_leaves" } are not used.

  warnings.warn(smsg, UserWarning)
/Library/Frameworks/Python.framework/Versions/3.8/lib/pytho

각 Fold의 정확도: [0.80654184 0.80817639 0.80654184 0.81082799 0.80826371 0.80897203
 0.80782782 0.80871776 0.80671994 0.81044315]
평균 정확도: 0.8083032472065967


/Library/Frameworks/Python.framework/Versions/3.8/lib/python3.8/site-packages/xgboost/core.py:160: UserWarning: [19:12:30] WARNING: /Users/runner/work/xgboost/xgboost/src/learner.cc:742: 
Parameters: { "num_leaves" } are not used.

  warnings.warn(smsg, UserWarning)


XGBClassifier(base_score=None, booster=None, callbacks=None,
              colsample_bylevel=None, colsample_bynode=None,
              colsample_bytree=0.89, device=None, early_stopping_rounds=None,
              enable_categorical=True, eval_metric=None, feature_types=None,
              gamma=None, grow_policy=None, importance_type=None,
              interaction_constraints=None, learning_rate=0.05, max_bin=None,
              max_cat_threshold=None, max_cat_to_onehot=None,
              max_delta_step=None, max_depth=8, max_leaves=None,
              min_child_weight=1, missing=nan, monotone_constraints=None,
              multi_strategy=None, n_estimators=500, n_jobs=None,
              num_leaves=128, num_parallel_tree=None, ...)